In [0]:
# spark basic imports
import pyspark
from pyspark.conf import SparkConf
from pyspark.sql.session import SparkSession
#import df_operations as df_op.
#import settings

# imports
import os
import pandas as pd
import pyspark.sql.functions as F
import itertools
import ast

# Modelos
from pyspark.ml import PipelineModel
from pyspark.ml.feature import StringIndexer, StringIndexerModel

In [0]:
sufijo="_2021"

In [0]:
tabla=f"tecnalia{sufijo}_csv"
modelsPath=f"/dbfs/FileStore/redec/tecnalia{sufijo}"
filePretatamientoNulos=os.path.join(modelsPath,f'tecnalia_mms_fillna{sufijo}.dct')
fileStringIndexer=os.path.join(modelsPath,f'tecnalia_StringIndexer{sufijo}.dct')
fileListToLen=os.path.join(modelsPath,f'tecnalia_StringToLen{sufijo}.lst')

In [0]:
print(tabla)
print(modelsPath)

tecnalia_2021_csv
/dbfs/FileStore/redec/tecnalia_2021

In [0]:
#import JerarquiaCovarianza as jc

In [0]:
#No ponemos configuracion. Ya estamos conectados aqui al spark directamente
spark

Out[6]:

SparkSession - hive 
 
 
 SparkContext 

 Spark UI 

 
 Version 
 v3.0.1 
 Master 
 spark://10.139.64.6:7077 
 AppName 
 Databricks Shell

In [0]:
sc

Out[7]:

SparkContext 

 Spark UI 

 
 Version 
 v3.0.1 
 Master 
 spark://10.139.64.6:7077 
 AppName 
 Databricks Shell

In [0]:
tramas_mms=[['cotp', 'eth', 'frame', 'ip', 'mms', 'pres', 'ses', 'tcp', 'tpkt', 'vssmonitoring'],
            ['data', 'eth', 'frame', 'ip', 'tcp', 'vssmonitoring']]
tramas_duda=['eth', 'frame', 'ip', 'tcp', 'vssmonitoring']

In [0]:
##Cargamos los datos
#Data

dfPreTrain=spark.sql(f"select * from {tabla}")

In [0]:
indexCol="_c0"
dtCol='timestamp'
dtCol='frame_time_epoch'

In [0]:
capasMMS = list()
for l in tramas_mms:
  capasMMS += l
  
capasMMS=list(set(capasMMS))

#Recopilar las columnas de las capas implicadas en los protocolos
colsMMS=list()
for p in capasMMS:
  colsMMS += [c for c in dfPreTrain.columns if c.startswith(p+"_")]
  
colsMMS +=['protocols']+[indexCol,dtCol]

protocols=[str(p) for p in tramas_mms]
print(capasMMS)
print(colsMMS)

print(protocols)

listProtocols="(\""+"\",\"".join(protocols)+"\")"

listProtocols

['frame', 'mms', 'ses', 'ip', 'tpkt', 'tcp', 'data', 'pres', 'vssmonitoring', 'cotp', 'eth']
['frame_cap_len', 'frame_encap_type', 'frame_ignored', 'frame_interface_id', 'frame_interface_name', 'frame_len', 'frame_marked', 'frame_number', 'frame_offset_shift', 'frame_protocols', 'frame_time', 'frame_time_delta', 'frame_time_delta_displayed', 'frame_time_epoch', 'frame_time_relative', 'mms_accessresult', 'mms_ber_bitstring_padding', 'mms_binary_time', 'mms_bit_string', 'mms_boolean', 'mms_confirmed_requestpdu_element', 'mms_confirmed_responsepdu_element', 'mms_confirmedservicerequest', 'mms_confirmedserviceresponse', 'mms_data', 'mms_domain_specific_element', 'mms_domainid', 'mms_floating_point', 'mms_informationreport_element', 'mms_integer', 'mms_invokeid', 'mms_itemid', 'mms_listofaccessresult', 'mms_listofvariable', 'mms_listofvariable_item_element', 'mms_name', 'mms_read_element', 'mms_structure', 'mms_success', 'mms_unconfirmed_pdu_element', 'mms_unconfirmedservice', 'mms_unsigned', 'mms_utc_time', 'mms_variableaccessspecification', 'mms_variableaccessspecificatn', 'mms_variablelistname', 'mms_variablespecification', 'mms_visible_string', 'mms_vmd_specific', 'ses_length', 'ses_type', 'ip_addr', 'ip_checksum', 'ip_checksum_status', 'ip_dsfield', 'ip_dsfield_dscp', 'ip_dsfield_ecn', 'ip_dst', 'ip_dst_host', 'ip_flags', 'ip_flags_df', 'ip_flags_mf', 'ip_flags_rb', 'ip_frag_offset', 'ip_hdr_len', 'ip_host', 'ip_id', 'ip_len', 'ip_proto', 'ip_src', 'ip_src_host', 'ip_ttl', 'ip_version', 'tpkt_continuation_data', 'tpkt_length', 'tpkt_reserved', 'tpkt_version', 'tcp__ws_expert', 'tcp__ws_expert_group', 'tcp__ws_expert_message', 'tcp__ws_expert_severity', 'tcp_ack', 'tcp_ack_raw', 'tcp_analysis', 'tcp_analysis_ack_lost_segment', 'tcp_analysis_ack_rtt', 'tcp_analysis_acks_frame', 'tcp_analysis_bytes_in_flight', 'tcp_analysis_duplicate_ack', 'tcp_analysis_duplicate_ack_frame', 'tcp_analysis_duplicate_ack_num', 'tcp_analysis_flags', 'tcp_analysis_initial_rtt', 'tcp_analysis_keep_alive', 'tcp_analysis_keep_alive_ack', 'tcp_analysis_lost_segment', 'tcp_analysis_out_of_order', 'tcp_analysis_push_bytes_sent', 'tcp_analysis_retransmission', 'tcp_analysis_rto', 'tcp_analysis_rto_frame', 'tcp_analysis_spurious_retransmission', 'tcp_analysis_window_update', 'tcp_checksum', 'tcp_checksum_status', 'tcp_connection_fin', 'tcp_connection_rst', 'tcp_connection_sack', 'tcp_connection_syn', 'tcp_dstport', 'tcp_flags', 'tcp_flags_ack', 'tcp_flags_cwr', 'tcp_flags_ecn', 'tcp_flags_fin', 'tcp_flags_ns', 'tcp_flags_push', 'tcp_flags_res', 'tcp_flags_reset', 'tcp_flags_str', 'tcp_flags_syn', 'tcp_flags_urg', 'tcp_hdr_len', 'tcp_len', 'tcp_nxtseq', 'tcp_option_kind', 'tcp_option_len', 'tcp_options', 'tcp_options_mss', 'tcp_options_mss_val', 'tcp_options_nop', 'tcp_options_sack', 'tcp_options_sack_count', 'tcp_options_sack_le', 'tcp_options_sack_perm', 'tcp_options_sack_re', 'tcp_options_timestamp', 'tcp_options_timestamp_tsecr', 'tcp_options_timestamp_tsval', 'tcp_options_wscale', 'tcp_options_wscale_multiplier', 'tcp_options_wscale_shift', 'tcp_payload', 'tcp_port', 'tcp_segment_data', 'tcp_seq', 'tcp_seq_raw', 'tcp_srcport', 'tcp_stream', 'tcp_time_delta', 'tcp_time_relative', 'tcp_urgent_pointer', 'tcp_window_size', 'tcp_window_size_scalefactor', 'tcp_window_size_value', 'data_data', 'data_len', 'pres_fully_encoded_data', 'pres_pdv_list_element', 'pres_presentation_context_identifier', 'pres_presentation_data_values', 'pres_user_data', 'vssmonitoring_srcport', 'cotp_destref', 'cotp_eot', 'cotp_li', 'cotp_tpdu_number', 'cotp_type', 'eth_addr', 'eth_addr_oui', 'eth_addr_oui_resolved', 'eth_addr_resolved', 'eth_dst', 'eth_dst_ig', 'eth_dst_lg', 'eth_dst_oui', 'eth_dst_oui_resolved', 'eth_dst_resolved', 'eth_ig', 'eth_lg', 'eth_padding', 'eth_src', 'eth_src_ig', 'eth_src_lg', 'eth_src_oui', 'eth_src_oui_resolved', 'eth_src_resolved', 'eth_type', 'protocols', '_c0', 'frame_time_epoch']
["['cotp', 'eth', 'frame', 'ip', 'mms', 'pres', 'ses', 'tcp', 'tpkt', '

In [0]:
spark.sql(f"select distinct protocols from {tabla} where protocols in {listProtocols}").show()

+---------+
protocols|
+---------+
+---------+

In [0]:
listCols=",".join(colsMMS)
dfTrain=spark.sql(f"select {listCols} from {tabla} where protocols in {listProtocols}")
dfTrain=spark.sql(f"select {listCols} from {tabla}")
#dfTrain=dfTrain.limit(1000)
dfTrain.show()
dfTrain.count()

+-------------+----------------+-------------+------------------+--------------------+---------+------------+------------+------------------+--------------------+--------------------+----------------+--------------------------+--------------------+-------------------+----------------+-------------------------+---------------+--------------+-----------+--------------------------------+---------------------------------+---------------------------+----------------------------+--------+---------------------------+------------+------------------+-----------------------------+-----------+------------+----------+----------------------+------------------+-------------------------------+--------+----------------+-------------+-----------+---------------------------+----------------------+------------+------------+-------------------------------+-----------------------------+--------------------+-------------------------+------------------+----------------+----------+--------+------------+-----------+------------------+----------+---------------+--------------+------------+------------+----------+-----------+-----------+-----------+--------------+----------+------------+----------+------+--------+------------+------------+------+----------+----------------------+-----------+-------------+------------+--------------+--------------------+----------------------+-----------------------+-------+-----------+------------+-----------------------------+--------------------+-----------------------+----------------------------+--------------------------+--------------------------------+------------------------------+------------------+------------------------+-----------------------+---------------------------+-------------------------+-------------------------+----------------------------+---------------------------+----------------+----------------------+------------------------------------+--------------------------+------------+-------------------+------------------+------------------+-------------------+------------------+-----------+----------+-------------+-------------+-------------+-------------+------------+--------------+-------------+---------------+-------------+-------------+-------------+-----------+-------+----------+---------------+--------------+--------------------+---------------+-------------------+---------------+----------------+----------------------+-------------------+---------------------+-------------------+---------------------+---------------------------+---------------------------+------------------+-----------------------------+------------------------+--------------------+--------+----------------+-------+-----------+-----------+----------+--------------+-----------------+------------------+---------------+---------------------------+---------------------+---------+--------+-----------------------+---------------------+------------------------------------+-----------------------------+--------------+---------------------+------------+--------+-------+----------------+----------+-----------------+------------+---------------------+-----------------+-----------------+----------+----------+-----------+--------------------+-----------------+------+------+--------------+-----------------+----------+----------+-----------+--------------------+-----------------+----------+---------+---+--------------------+
frame_cap_len|frame_encap_type|frame_ignored|frame_interface_id|frame_interface_name|frame_len|frame_marked|frame_number|frame_offset_shift| frame_protocols| frame_time|frame_time_delta|frame_time_delta_displayed| frame_time_epoch|frame_time_relative|mms_accessresult|mms_ber_bitstring_padding|mms_binary_time|mms_bit_string|mms_boolean|mms_confirmed_requestpdu_element|mms_confirmed_responsepdu_element|mms_confirmedservicerequest|mms_confirmedserviceresponse|mms_data|mms_domain_specific_element|mms_domainid|mms_floating_point|mms_informationreport_element|mms_integer|mms_invokeid|mms_itemid|mms_listofaccessresult|mms_lis

In [0]:
#Pipeline para indexacion de Strings

from pyspark.ml import PipelineModel

f=open(fileStringIndexer,"r")
dctIndexers=ast.literal_eval(f.read())
f.close()

modelName=dctIndexers['StringIndex']
model=PipelineModel.load(modelName)

dctIndexers.update({'StringIndex': model})

dctIndexers

indexerPipeline=model

In [0]:
indexerPipeline.stages

Out[15]: [StringIndexerModel: uid=StringIndexer_1619b118afc4, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_3b20485dbf28, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_9847044d68ff, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_eb7138076626, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_1e365637d302, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_5ea4ca2c16af, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_2e9e0a3aca2e, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_1e901c808e24, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_92a47d0e0edb, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_dd717e77efb3, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_d122056bc112, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_24f441672bbf, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_d172d40f1fc1, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_23dbf20d289d, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_6dc0acb7cf03, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_fc8f0657b859, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_5dd07c51abf0, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_c44ffc2da018, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_6d5079d3fd90, handleInvalid=keep,
 StringIndexerModel: uid=StringIndexer_eae5172d61fd, handleInvalid=keep]

In [0]:
import ast
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import StandardScaler,StandardScalerModel
from pyspark.ml.clustering import KMeans, KMeansModel

f=open(os.path.join(modelsPath,f"jerarquia{sufijo}"),"r")   
strJerarquia=f.read()
f.close()

def loadModel(path):
    model=None
    if 'Scaler' in path:
        model=StandardScalerModel.load(path)
    if 'KMeans' in path:
        model=KMeansModel.load(path)
    if 'Vector' in path:
         model=VectorAssembler.load(path)
    return model
       
tJerarquia=ast.literal_eval(strJerarquia)
tJerarquia
redecJerarquia={}
for niv in tJerarquia.keys():
    if 'group' in str(niv): continue
    jn=tJerarquia[niv]
    redecJerarquia.update({niv:None})
    nivelDict={'vars':jn['vars']}
    #Cargar Assembler
    model=loadModel(jn['assembler'])
    nivelDict.update({'assembler':model})
    #Cargar Scaler
    model=loadModel(jn['scaler'])
    nivelDict.update({'scaler':model})
    #Cargar KMeans
    model=loadModel(jn['kmeans_model'])
    nivelDict.update({'kmeans_model':model})
    clusterDict={}
    for subNiv in jn['clusters_stats'].keys():
        subNivDict={}
        #Assembler
        ass=jn['clusters_stats'][subNiv]['assembler']
        subModel=loadModel(ass)
        subNivDict.update({"assembler":subModel})
        #Scaler
        sca=jn['clusters_stats'][subNiv]['scaler']
        subModel=loadModel(sca)        
        subNivDict.update({"scaler":subModel})
        
        clusterDict.update({subNiv:subNivDict})
        
    nivelDict.update({"clusters_stats":clusterDict})
    
    redecJerarquia.update({niv:nivelDict})

#Add grouped stats
tjgroup=tJerarquia['groups']
#Assembler
ass=tjgroup['assembler']
subModel=loadModel(ass)
tjgroup.update({'assembler':subModel})
#Scaler
sca=tjgroup['scaler']
subModel=loadModel(sca)
tjgroup.update({'scaler':subModel})

redecJerarquia.update({'groups':tjgroup})

redecJerarquia

Out[16]: {0: {'vars': ['_c0', 'eth_type', 'ip_src_host'],
 'assembler': VectorAssembler_95fc1fc40eae,
 'scaler': StandardScalerModel: uid=StandardScaler_413dc017da71, numFeatures=2, withMean=true, withStd=true,
 'kmeans_model': KMeansModel: uid=KMeans_a2a196867321, k=11, distanceMeasure=euclidean, numFeatures=2,
 'clusters_stats': {1: {'assembler': VectorAssembler_da8b9294e3d1,
 'scaler': StandardScalerModel: uid=StandardScaler_16488065b42c, numFeatures=2, withMean=true, withStd=true},
 6: {'assembler': VectorAssembler_a4611e260673,
 'scaler': StandardScalerModel: uid=StandardScaler_d79466d8826d, numFeatures=2, withMean=true, withStd=true},
 3: {'assembler': VectorAssembler_613f39a37720,
 'scaler': StandardScalerModel: uid=StandardScaler_c4f732e702f7, numFeatures=2, withMean=true, withStd=true},
 5: {'assembler': VectorAssembler_9ac84f1dc105,
 'scaler': StandardScalerModel: uid=StandardScaler_add6f4760f1c, numFeatures=2, withMean=true, withStd=true},
 9: {'assembler': VectorAssembler_a700320ba469,
 'scaler': StandardScalerModel: uid=StandardScaler_e9e495e8131c, numFeatures=2, withMean=true, withStd=true},
 4: {'assembler': VectorAssembler_7c83b4f04332,
 'scaler': StandardScalerModel: uid=StandardScaler_283f3d364d7b, numFeatures=2, withMean=true, withStd=true},
 8: {'assembler': VectorAssembler_54199415c00c,
 'scaler': StandardScalerModel: uid=StandardScaler_f8ec95427730, numFeatures=2, withMean=true, withStd=true},
 7: {'assembler': VectorAssembler_08b7759b4ce4,
 'scaler': StandardScalerModel: uid=StandardScaler_2d001e36965a, numFeatures=2, withMean=true, withStd=true},
 10: {'assembler': VectorAssembler_fc4ede3915b3,
 'scaler': StandardScalerModel: uid=StandardScaler_f654ff7606e1, numFeatures=2, withMean=true, withStd=true},
 2: {'assembler': VectorAssembler_993e0e4e5789,
 'scaler': StandardScalerModel: uid=StandardScaler_8a2547289d4c, numFeatures=2, withMean=true, withStd=true},
 0: {'assembler': VectorAssembler_555118b84d05,
 'scaler': StandardScalerModel: uid=StandardScaler_8c0a29a5522e, numFeatures=2, withMean=true, withStd=true}}},
 1: {'vars': ['_c0',
 'eth_src_resolved',
 'frame_cap_len',
 'ip_len',
 'tcp_len',
 'tcp_seq_raw',
 'tcp_window_size',
 'tcp_window_size_scalefactor'],
 'assembler': VectorAssembler_7fa13bcf2b57,
 'scaler': StandardScalerModel: uid=StandardScaler_bb5817926366, numFeatures=7, withMean=true, withStd=true,
 'kmeans_model': KMeansModel: uid=KMeans_f16919a778e8, k=4, distanceMeasure=euclidean, numFeatures=7,
 'clusters_stats': {1: {'assembler': VectorAssembler_48f5fc893479,
 'scaler': StandardScalerModel: uid=StandardScaler_3e2c70fcb4df, numFeatures=7, withMean=true, withStd=true},
 3: {'assembler': VectorAssembler_590473ce038d,
 'scaler': StandardScalerModel: uid=StandardScaler_c17ee3e6e54c, numFeatures=7, withMean=true, withStd=true},
 2: {'assembler': VectorAssembler_6a7d4afaa629,
 'scaler': StandardScalerModel: uid=StandardScaler_e90885a13924, numFeatures=7, withMean=true, withStd=true},
 0: {'assembler': VectorAssembler_8718d0636f02,
 'scaler': StandardScalerModel: uid=StandardScaler_27ab5cc22866, numFeatures=7, withMean=true, withStd=true}}},
 2: {'vars': ['_c0',
 'eth_addr_resolved',
 'eth_dst',
 'eth_padding',
 'eth_src',
 'frame_len',
 'tcp_analysis',
 'tcp_port',
 'tcp_seq'],
 'assembler': VectorAssembler_74d2889fa262,
 'scaler': StandardScalerModel: uid=StandardScaler_2ff2f64ff50c, numFeatures=8, withMean=true, withStd=true,
 'kmeans_model': KMeansModel: uid=KMeans_81376704e3fe, k=12, distanceMeasure=euclidean, numFeatures=8,
 'clusters_stats': {1: {'assembler': VectorAssembler_1301ba1d32c4,
 'scaler': StandardScalerModel: uid=StandardScaler_e094326785a9, numFeatures=8, withMean=true, withStd=true},
 6: {'assembler': VectorAssembler_f306f4594abe,
 'scaler': StandardScalerModel: uid=StandardScaler_253ee66e33c9, numFeatures=8, withMean=true, withStd=true},
 3: {'assembler': VectorAssembler_e3787954276e,
 'scaler': StandardScalerModel: uid=StandardScaler_7ef386eebf49, numFeatures=8, withMea

In [0]:
inPipeline=list()
for m in indexerPipeline.stages:
  print (m.getInputCol())
  inPipeline.append(m.getInputCol())
  
inPipeline

eth_addr
eth_addr_resolved
eth_dst
eth_dst_resolved
eth_padding
eth_src
eth_src_resolved
eth_type
frame_interface_name
frame_protocols
ip_addr
ip_dsfield
ip_dst
ip_dst_host
ip_flags
ip_host
ip_src
ip_src_host
tcp_analysis
tcp_flags
Out[17]: ['eth_addr',
 'eth_addr_resolved',
 'eth_dst',
 'eth_dst_resolved',
 'eth_padding',
 'eth_src',
 'eth_src_resolved',
 'eth_type',
 'frame_interface_name',
 'frame_protocols',
 'ip_addr',
 'ip_dsfield',
 'ip_dst',
 'ip_dst_host',
 'ip_flags',
 'ip_host',
 'ip_src',
 'ip_src_host',
 'tcp_analysis',
 'tcp_flags']

In [0]:
redecJerarquia

listaVars=list()
for niv in redecJerarquia.keys():
  if niv=='groups': continue
  listaVars+=redecJerarquia[niv]['vars']
  
listaVars=list(set(listaVars))

lengths = [c for c in listaVars if c.endswith("_leng")]

sinLen = [c for c in listaVars if not c.endswith("_leng")]

listaVars=sinLen + [c[:-5] for c in lengths] + inPipeline
listaVars=list(set(listaVars))

listaVars

Out[18]: ['tcp_len',
 'ip_dst',
 'frame_protocols',
 'tcp_port',
 'ip_flags',
 'tcp_analysis',
 'eth_addr',
 'ip_host',
 'frame_interface_name',
 'tcp_flags',
 'tcp_seq',
 'eth_padding',
 'frame_len',
 'ip_addr',
 'tcp_window_size_scalefactor',
 'ip_dsfield',
 'ip_len',
 'tcp_window_size',
 'ip_dst_host',
 'eth_src_resolved',
 'eth_dst_resolved',
 'tcp_seq_raw',
 'eth_addr_resolved',
 'eth_type',
 '_c0',
 'ip_src',
 'eth_src',
 'vssmonitoring_srcport',
 'frame_cap_len',
 'eth_dst',
 'ip_src_host']

In [0]:
#Seleccionar solo las variables implicadas en los niveles que son las que se van a analizar
df=dfTrain.select(listaVars)

In [0]:
df_r=indexerPipeline.transform(df)
print(df_r.columns)
indexadas=[c for c in df_r.columns if c.endswith('_index')]+[c.replace('_index','') for c in df_r.columns if c.endswith('_index')]
df_r.select(indexadas).show()


['tcp_len', 'ip_dst', 'frame_protocols', 'tcp_port', 'ip_flags', 'tcp_analysis', 'eth_addr', 'ip_host', 'frame_interface_name', 'tcp_flags', 'tcp_seq', 'eth_padding', 'frame_len', 'ip_addr', 'tcp_window_size_scalefactor', 'ip_dsfield', 'ip_len', 'tcp_window_size', 'ip_dst_host', 'eth_src_resolved', 'eth_dst_resolved', 'tcp_seq_raw', 'eth_addr_resolved', 'eth_type', '_c0', 'ip_src', 'eth_src', 'vssmonitoring_srcport', 'frame_cap_len', 'eth_dst', 'ip_src_host', 'eth_addr_index', 'eth_addr_resolved_index', 'eth_dst_index', 'eth_dst_resolved_index', 'eth_padding_index', 'eth_src_index', 'eth_src_resolved_index', 'eth_type_index', 'frame_interface_name_index', 'frame_protocols_index', 'ip_addr_index', 'ip_dsfield_index', 'ip_dst_index', 'ip_dst_host_index', 'ip_flags_index', 'ip_host_index', 'ip_src_index', 'ip_src_host_index', 'tcp_analysis_index', 'tcp_flags_index']
+--------------+-----------------------+-------------+----------------------+-----------------+-------------+----------------------+--------------+--------------------------+---------------------+-------------+----------------+------------+-----------------+--------------+-------------+------------+-----------------+------------------+---------------+-----------------+-----------------+-----------------+-----------------+--------------+-----------------+-----------------+----------+--------------------+--------------------+------------+----------+------------+------------+----------+------------+------------+------------+------------+----------+
eth_addr_index|eth_addr_resolved_index|eth_dst_index|eth_dst_resolved_index|eth_padding_index|eth_src_index|eth_src_resolved_index|eth_type_index|frame_interface_name_index|frame_protocols_index|ip_addr_index|ip_dsfield_index|ip_dst_index|ip_dst_host_index|ip_flags_index|ip_host_index|ip_src_index|ip_src_host_index|tcp_analysis_index|tcp_flags_index| eth_addr|eth_addr_resolved| eth_dst| eth_dst_resolved| eth_padding| eth_src| eth_src_resolved| eth_type|frame_interface_name| frame_protocols| ip_addr|ip_dsfield| ip_dst| ip_dst_host| ip_flags| ip_host| ip_src| ip_src_host|tcp_analysis| tcp_flags|
+--------------+-----------------------+-------------+----------------------+-----------------+-------------+----------------------+--------------+--------------------------+---------------------+-------------+----------------+------------+-----------------+--------------+-------------+------------+-----------------+------------------+---------------+-----------------+-----------------+-----------------+-----------------+--------------+-----------------+-----------------+----------+--------------------+--------------------+------------+----------+------------+------------+----------+------------+------------+------------+------------+----------+
 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|12:46:f0:5e:a6:32|12:46:f0:5e:a6:32|01:15:4e:00:01:00| Iec_00:01:00| null|12:46:f0:5e:a6:32|12:46:f0:5e:a6:32|0x000088fb| eth0|eth:ethertype:hsr...| null| null| null| null| null| null| null| null| null| null|
 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|12:46:f0:5e:a6:32|12:46:f0:5e:a6:32|01:15:4e:00:01:00| Iec_00:01:00| null|12:46:f0:5e:a6:32|12:46:f0:5e:a6:32|0x000088fb| eth0|eth:ethertype:hsr...| null| null| null| null| null| null| null| null| null| null|
 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|12:46:f0:5e:a6:32|12:46:f0:5e:a6:32|01:15:4e:00:01:00| Iec_00:01:00| null|12:46:f0:5e:a6:32|12:46:f0:5e:a6:32|0x000088fb| eth0|eth:ethertype:hsr...| null| null| null| null| null| null| null| null| null| null|
 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|12:46:f0:5e:a6:32|12:46:f0:5e:a6:32|01:15:4e:00:01:00| Iec_00:01:00| null|12:46:f0:5e:a6:32|12:46:f0:5e:a6:32|0x000088fb| eth0|eth:ethertype:hsr...| null| null| null| null| null| null| nul

In [0]:
print([c for c in df_r.columns if c.endswith('index')])

['eth_addr_index', 'eth_addr_resolved_index', 'eth_dst_index', 'eth_dst_resolved_index', 'eth_padding_index', 'eth_src_index', 'eth_src_resolved_index', 'eth_type_index', 'frame_interface_name_index', 'frame_protocols_index', 'ip_addr_index', 'ip_dsfield_index', 'ip_dst_index', 'ip_dst_host_index', 'ip_flags_index', 'ip_host_index', 'ip_src_index', 'ip_src_host_index', 'tcp_analysis_index', 'tcp_flags_index']

In [0]:
indexedColumns=[c.replace("_index","") for c in df_r.columns if c.endswith("index")]
print(indexedColumns)

for c in indexedColumns:
  df_r=df_r.drop(c)
  df_r=df_r.withColumnRenamed(c+"_index",c)
  
for c in lengths:
  c=c[:-5]
  df_r=df_r.withColumn(c+"_leng",F.length(F.col(c)))
  df_r=df_r.drop(c)

['eth_addr', 'eth_addr_resolved', 'eth_dst', 'eth_dst_resolved', 'eth_padding', 'eth_src', 'eth_src_resolved', 'eth_type', 'frame_interface_name', 'frame_protocols', 'ip_addr', 'ip_dsfield', 'ip_dst', 'ip_dst_host', 'ip_flags', 'ip_host', 'ip_src', 'ip_src_host', 'tcp_analysis', 'tcp_flags']

In [0]:
#Columnas con datos que se transforman en longitud por ser muy variables y muy largos
f=open(fileListToLen)
strColsNotIndex=ast.literal_eval(f.read())
f.close()

print(strColsNotIndex)

strColsNotIndex = [c for c in strColsNotIndex if c in df_r.columns]

strColsNotIndex


['frame_time', 'ip_checksum', 'ip_id', 'tcp_checksum', 'tcp_payload']
Out[23]: []

In [0]:
#Valores no relevantes
no_relevantes = ['timestamp']
df_r = df_r.drop(*no_relevantes)

In [0]:
'''from pyspark.sql.functions import monotonically_increasing_id 

df_k = df_r.withColumn("id", monotonically_increasing_id())
indexCol = '_c0'
'''

Out[25]: 'from pyspark.sql.functions import monotonically_increasing_id \n\ndf_k = df_r.withColumn("id", monotonically_increasing_id())\nindexCol = \'_c0\'\n'

In [0]:
from pyspark.sql.functions import avg, max, col
import ast

#Obtenemos la configuración de los nulos del modelado
f=open(filePretatamientoNulos,"r")
dct=f.read()
dctFillNa=ast.literal_eval(dct)

print(type(dctFillNa))


<class 'dict'>

In [0]:
dctFillNa

Out[27]: {'eth_ig': -0.0,
 'eth_lg': -1.0,
 'frame_cap_len': -933.0,
 'frame_encap_type': -1.0,
 'frame_ignored': -0.0,
 'frame_interface_id': -0.0,
 'frame_len': -933.0,
 'frame_marked': -0.0,
 'frame_number': -250407.0,
 'frame_offset_shift': -0.0,
 'frame_time_delta': -0.666508229,
 'frame_time_delta_displayed': -0.666508229,
 'frame_time_relative': -3599.768631075,
 'ip_frag_offset': -0.0,
 'ip_hdr_len': -20.0,
 'ip_len': -913.0,
 'ip_proto': -17.0,
 'ip_ttl': -255.0,
 'ip_version': -6.0,
 'tcp_ack': -1915693.0,
 'tcp_ack_raw': -3635278230.0,
 'tcp_dstport': -49678.0,
 'tcp_hdr_len': -32.0,
 'tcp_len': -873.0,
 'tcp_nxtseq': -1915693.0,
 'tcp_port': -49678.0,
 'tcp_seq': -1914902.0,
 'tcp_seq_raw': -3635278230.0,
 'tcp_srcport': -49678.0,
 'tcp_stream': -4.0,
 'tcp_time_delta': -2.075788489,
 'tcp_time_relative': -3599.053988315,
 'tcp_urgent_pointer': -0.0,
 'tcp_window_size': -65535.0,
 'tcp_window_size_scalefactor': 1.0,
 'tcp_window_size_value': -65535.0,
 'vssmonitoring_srcport': -62370.0,
 'eth_addr': -14.0,
 'eth_addr_resolved': -14.0,
 'eth_dst': -14.0,
 'eth_dst_resolved': -14.0,
 'eth_padding': -7.0,
 'eth_src': -14.0,
 'eth_src_resolved': -14.0,
 'eth_type': -7.0,
 'frame_interface_name': -0.0,
 'frame_protocols': -17.0,
 'ip_addr': -9.0,
 'ip_dsfield': -1.0,
 'ip_dst': -9.0,
 'ip_dst_host': -9.0,
 'ip_flags': -2.0,
 'ip_host': -9.0,
 'ip_src': -6.0,
 'ip_src_host': -6.0,
 'tcp_analysis': -1.0,
 'tcp_flags': -2.0,
 'frame_time_leng': -54.0,
 'ip_checksum_leng': -10.0,
 'ip_id_leng': -10.0,
 'tcp_checksum_leng': -10.0,
 'tcp_payload_leng': -2618.0}

In [0]:
#Eliminar del diccionario las columnas que se han descartado por no estar en los niveles

keysToRemove = [c for c in dctFillNa.keys() if c not in df_r.columns]
print(keysToRemove)

for k in keysToRemove:del dctFillNa[k]


['eth_ig', 'eth_lg', 'frame_encap_type', 'frame_ignored', 'frame_interface_id', 'frame_marked', 'frame_number', 'frame_offset_shift', 'frame_time_delta', 'frame_time_delta_displayed', 'frame_time_relative', 'ip_frag_offset', 'ip_hdr_len', 'ip_proto', 'ip_ttl', 'ip_version', 'tcp_ack', 'tcp_ack_raw', 'tcp_dstport', 'tcp_hdr_len', 'tcp_nxtseq', 'tcp_srcport', 'tcp_stream', 'tcp_time_delta', 'tcp_time_relative', 'tcp_urgent_pointer', 'tcp_window_size_value', 'frame_time_leng', 'ip_checksum_leng', 'ip_id_leng', 'tcp_checksum_leng', 'tcp_payload_leng']

In [0]:
dctFillNa

Out[29]: {'frame_cap_len': -933.0,
 'frame_len': -933.0,
 'ip_len': -913.0,
 'tcp_len': -873.0,
 'tcp_port': -49678.0,
 'tcp_seq': -1914902.0,
 'tcp_seq_raw': -3635278230.0,
 'tcp_window_size': -65535.0,
 'tcp_window_size_scalefactor': 1.0,
 'vssmonitoring_srcport': -62370.0,
 'eth_addr': -14.0,
 'eth_addr_resolved': -14.0,
 'eth_dst': -14.0,
 'eth_dst_resolved': -14.0,
 'eth_padding': -7.0,
 'eth_src': -14.0,
 'eth_src_resolved': -14.0,
 'eth_type': -7.0,
 'frame_interface_name': -0.0,
 'frame_protocols': -17.0,
 'ip_addr': -9.0,
 'ip_dsfield': -1.0,
 'ip_dst': -9.0,
 'ip_dst_host': -9.0,
 'ip_flags': -2.0,
 'ip_host': -9.0,
 'ip_src': -6.0,
 'ip_src_host': -6.0,
 'tcp_analysis': -1.0,
 'tcp_flags': -2.0}

In [0]:
df_k=df_r.na.fill(dctFillNa)
df_k.show()

+-------+--------+--------+---------+---------------------------+------+---------------+-----------+---+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+
tcp_len|tcp_port| tcp_seq|frame_len|tcp_window_size_scalefactor|ip_len|tcp_window_size|tcp_seq_raw|_c0|vssmonitoring_srcport|frame_cap_len|eth_addr|eth_addr_resolved|eth_dst|eth_dst_resolved|eth_padding|eth_src|eth_src_resolved|eth_type|frame_interface_name|frame_protocols|ip_addr|ip_dsfield|ip_dst|ip_dst_host|ip_flags|ip_host|ip_src|ip_src_host|tcp_analysis|tcp_flags|
+-------+--------+--------+---------+---------------------------+------+---------------+-----------+---+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 1| -62370| 66| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 2| -62370| 66| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 3| -62370| 66| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 4| -62370| 66| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 5| -62370| 66| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 6| -62370| 66| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 7| -62370| 66| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 8| -62370| 66| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 9| 53371| 66| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 10| 53371| 66| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 11| 53371| 66| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 12| 53372| 66| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 13| 53372| 66| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 14| 53372| 66| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 1| 102| 1| 66| -1| 41| 2050| 3635223018| 15| 25430| 66| 0.0| 0.0| 8.0| 8.0| 4.0| 0.0| 0.0| 0.0| 0.0| 15.0| 4.0| 0.0| 4.0| 4.0| 0.0| 4.0| 0.0| 0.0| 0.0| 0.0|
 0| 49678| 1| 72| -1| 52| 3456| 125902804| 16| 27523| 72| 8.0| 8.0| 2.0| 2.0| 7.0| 8.0| 8.0| 0.0| 0.0| 1.0| 0.0| 0.0| 0.0| 0.0| 0.0| 0.0| 4.0| 4.0| 0.0| 0.0|
 -873| -49678|-1914902| 66| 1| -913| -65535|-3635278230| 17| -62370| 66| 12.0| 12.0| 7.0| 7.0| 7.0| 12.0| 12.0| 4.0| 0.0| 8.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.

In [0]:
from pyspark.sql.functions import *

df_k.select([count(when(isnan(c) | col(c).isNull(), c)).alias(c) for c in df_k.columns]).toPandas()

Out[31]:

tcp_len 
 tcp_port 
 tcp_seq 
 frame_len 
 tcp_window_size_scalefactor 
 ip_len 
 tcp_window_size 
 tcp_seq_raw 
 _c0 
 vssmonitoring_srcport 
 frame_cap_len 
 eth_addr 
 eth_addr_resolved 
 eth_dst 
 eth_dst_resolved 
 eth_padding 
 eth_src 
 eth_src_resolved 
 eth_type 
 frame_interface_name 
 frame_protocols 
 ip_addr 
 ip_dsfield 
 ip_dst 
 ip_dst_host 
 ip_flags 
 ip_host 
 ip_src 
 ip_src_host 
 tcp_analysis 
 tcp_flags 
 
 
 
 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0

In [0]:
dataCols = df_k.columns
dataCols.remove(indexCol)
#df_k.describe()

In [0]:
from pyspark.sql.types import DoubleType
dataCols = df_k.columns
dataCols.remove(indexCol)
for c in dataCols:
    df_col = df_k.select(c).filter(F.col(c).isNull())
    df_k=df_k.withColumn(c,col(c).cast(DoubleType()))
    '''print(c, "esta limpio")
    else:
        print(df_k.select(c).dtypes)
        print(c, "tiene nulos")
    print(df_k.select(c).dtypes)
    '''

In [0]:
df_k.dtypes

Out[34]: [('tcp_len', 'double'),
 ('tcp_port', 'double'),
 ('tcp_seq', 'double'),
 ('frame_len', 'double'),
 ('tcp_window_size_scalefactor', 'double'),
 ('ip_len', 'double'),
 ('tcp_window_size', 'double'),
 ('tcp_seq_raw', 'double'),
 ('_c0', 'int'),
 ('vssmonitoring_srcport', 'double'),
 ('frame_cap_len', 'double'),
 ('eth_addr', 'double'),
 ('eth_addr_resolved', 'double'),
 ('eth_dst', 'double'),
 ('eth_dst_resolved', 'double'),
 ('eth_padding', 'double'),
 ('eth_src', 'double'),
 ('eth_src_resolved', 'double'),
 ('eth_type', 'double'),
 ('frame_interface_name', 'double'),
 ('frame_protocols', 'double'),
 ('ip_addr', 'double'),
 ('ip_dsfield', 'double'),
 ('ip_dst', 'double'),
 ('ip_dst_host', 'double'),
 ('ip_flags', 'double'),
 ('ip_host', 'double'),
 ('ip_src', 'double'),
 ('ip_src_host', 'double'),
 ('tcp_analysis', 'double'),
 ('tcp_flags', 'double')]

In [0]:
try:
    spark.sql(f"drop table Tecnalia_tratado{sufijo}")
except:
    print(f"No existe la tabla Tecnalia_tratado{sufijo}")

df_k.createOrReplaceTempView("mytempTable")
spark.sql(f"create table Tecnalia_tratado{sufijo} as select * from mytempTable")


Out[35]: DataFrame[]

In [0]:
import ast
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import StandardScaler,StandardScalerModel
from pyspark.ml.clustering import KMeans, KMeansModel

f=open(os.path.join(modelsPath,f"jerarquia{sufijo}"),"r")   
strJerarquia=f.read()
f.close()

def loadModel(path):
    model=None
    if 'Scaler' in path:
        model=StandardScalerModel.load(path)
    if 'KMeans' in path:
        model=KMeansModel.load(path)
    if 'Vector' in path:
         model=VectorAssembler.load(path)
    return model
       
tJerarquia=ast.literal_eval(strJerarquia)
tJerarquia
redecJerarquia={}
for niv in tJerarquia.keys():
    if 'group' in str(niv): continue
    jn=tJerarquia[niv]
    redecJerarquia.update({niv:None})
    nivelDict={'vars':jn['vars']}
    #Cargar Assembler
    model=loadModel(jn['assembler'])
    nivelDict.update({'assembler':model})
    #Cargar Scaler
    model=loadModel(jn['scaler'])
    nivelDict.update({'scaler':model})
    #Cargar KMeans
    model=loadModel(jn['kmeans_model'])
    nivelDict.update({'kmeans_model':model})
    clusterDict={}
    for subNiv in jn['clusters_stats'].keys():
        subNivDict={}
        #Assembler
        ass=jn['clusters_stats'][subNiv]['assembler']
        subModel=loadModel(ass)
        subNivDict.update({"assembler":subModel})
        #Scaler
        sca=jn['clusters_stats'][subNiv]['scaler']
        subModel=loadModel(sca)        
        subNivDict.update({"scaler":subModel})
        
        clusterDict.update({subNiv:subNivDict})
        
    nivelDict.update({"clusters_stats":clusterDict})
    
    redecJerarquia.update({niv:nivelDict})

#Add grouped stats
tjgroup=tJerarquia['groups']
#Assembler
ass=tjgroup['assembler']
subModel=loadModel(ass)
tjgroup.update({'assembler':subModel})
#Scaler
sca=tjgroup['scaler']
subModel=loadModel(sca)
tjgroup.update({'scaler':subModel})

redecJerarquia.update({'groups':tjgroup})

    

In [0]:
redecJerarquia

Out[37]: {0: {'vars': ['_c0', 'eth_type', 'ip_src_host'],
 'assembler': VectorAssembler_95fc1fc40eae,
 'scaler': StandardScalerModel: uid=StandardScaler_413dc017da71, numFeatures=2, withMean=true, withStd=true,
 'kmeans_model': KMeansModel: uid=KMeans_a2a196867321, k=11, distanceMeasure=euclidean, numFeatures=2,
 'clusters_stats': {1: {'assembler': VectorAssembler_da8b9294e3d1,
 'scaler': StandardScalerModel: uid=StandardScaler_16488065b42c, numFeatures=2, withMean=true, withStd=true},
 6: {'assembler': VectorAssembler_a4611e260673,
 'scaler': StandardScalerModel: uid=StandardScaler_d79466d8826d, numFeatures=2, withMean=true, withStd=true},
 3: {'assembler': VectorAssembler_613f39a37720,
 'scaler': StandardScalerModel: uid=StandardScaler_c4f732e702f7, numFeatures=2, withMean=true, withStd=true},
 5: {'assembler': VectorAssembler_9ac84f1dc105,
 'scaler': StandardScalerModel: uid=StandardScaler_add6f4760f1c, numFeatures=2, withMean=true, withStd=true},
 9: {'assembler': VectorAssembler_a700320ba469,
 'scaler': StandardScalerModel: uid=StandardScaler_e9e495e8131c, numFeatures=2, withMean=true, withStd=true},
 4: {'assembler': VectorAssembler_7c83b4f04332,
 'scaler': StandardScalerModel: uid=StandardScaler_283f3d364d7b, numFeatures=2, withMean=true, withStd=true},
 8: {'assembler': VectorAssembler_54199415c00c,
 'scaler': StandardScalerModel: uid=StandardScaler_f8ec95427730, numFeatures=2, withMean=true, withStd=true},
 7: {'assembler': VectorAssembler_08b7759b4ce4,
 'scaler': StandardScalerModel: uid=StandardScaler_2d001e36965a, numFeatures=2, withMean=true, withStd=true},
 10: {'assembler': VectorAssembler_fc4ede3915b3,
 'scaler': StandardScalerModel: uid=StandardScaler_f654ff7606e1, numFeatures=2, withMean=true, withStd=true},
 2: {'assembler': VectorAssembler_993e0e4e5789,
 'scaler': StandardScalerModel: uid=StandardScaler_8a2547289d4c, numFeatures=2, withMean=true, withStd=true},
 0: {'assembler': VectorAssembler_555118b84d05,
 'scaler': StandardScalerModel: uid=StandardScaler_8c0a29a5522e, numFeatures=2, withMean=true, withStd=true}}},
 1: {'vars': ['_c0',
 'eth_src_resolved',
 'frame_cap_len',
 'ip_len',
 'tcp_len',
 'tcp_seq_raw',
 'tcp_window_size',
 'tcp_window_size_scalefactor'],
 'assembler': VectorAssembler_7fa13bcf2b57,
 'scaler': StandardScalerModel: uid=StandardScaler_bb5817926366, numFeatures=7, withMean=true, withStd=true,
 'kmeans_model': KMeansModel: uid=KMeans_f16919a778e8, k=4, distanceMeasure=euclidean, numFeatures=7,
 'clusters_stats': {1: {'assembler': VectorAssembler_48f5fc893479,
 'scaler': StandardScalerModel: uid=StandardScaler_3e2c70fcb4df, numFeatures=7, withMean=true, withStd=true},
 3: {'assembler': VectorAssembler_590473ce038d,
 'scaler': StandardScalerModel: uid=StandardScaler_c17ee3e6e54c, numFeatures=7, withMean=true, withStd=true},
 2: {'assembler': VectorAssembler_6a7d4afaa629,
 'scaler': StandardScalerModel: uid=StandardScaler_e90885a13924, numFeatures=7, withMean=true, withStd=true},
 0: {'assembler': VectorAssembler_8718d0636f02,
 'scaler': StandardScalerModel: uid=StandardScaler_27ab5cc22866, numFeatures=7, withMean=true, withStd=true}}},
 2: {'vars': ['_c0',
 'eth_addr_resolved',
 'eth_dst',
 'eth_padding',
 'eth_src',
 'frame_len',
 'tcp_analysis',
 'tcp_port',
 'tcp_seq'],
 'assembler': VectorAssembler_74d2889fa262,
 'scaler': StandardScalerModel: uid=StandardScaler_2ff2f64ff50c, numFeatures=8, withMean=true, withStd=true,
 'kmeans_model': KMeansModel: uid=KMeans_81376704e3fe, k=12, distanceMeasure=euclidean, numFeatures=8,
 'clusters_stats': {1: {'assembler': VectorAssembler_1301ba1d32c4,
 'scaler': StandardScalerModel: uid=StandardScaler_e094326785a9, numFeatures=8, withMean=true, withStd=true},
 6: {'assembler': VectorAssembler_f306f4594abe,
 'scaler': StandardScalerModel: uid=StandardScaler_253ee66e33c9, numFeatures=8, withMean=true, withStd=true},
 3: {'assembler': VectorAssembler_e3787954276e,
 'scaler': StandardScalerModel: uid=StandardScaler_7ef386eebf49, numFeatures=8, withMea

In [0]:
from pyspark.sql.functions import monotonically_increasing_id
def paste_DF(sdf1, sdf2):
    print("PASTE ENTRADA ")
    sdf1.show()
    sdf2.show()
    print("PASTE ID")
    sdf1 = sdf1.withColumn("id", monotonically_increasing_id())

    sdf2 = sdf1.withColumn("id", monotonically_increasing_id())

    sdf1.show()

    sdf2.show()

    df3 = sdf1.join(sdf2, "id", "outer").drop("id")
    print("PASTE RESULTADO ")
    df3.show()
    return df3

    print("PASTE DF ")
    print("Add ROW_NUMBER")
    sdf1 = sdf1.withColumn("row_number", F.row_number().over(Window.partitionBy().orderBy(lit('A'))))
    sdf2 = sdf2.withColumn("row_number", F.row_number().over(Window.partitionBy().orderBy(lit('A'))))        
    #sdf1.show()
    #sdf2.show()
    #new_schema = sdf1.join(sdf2,sdf1.row_number==sdf2.row_number,'inner').drop(sdf1.row_number).drop(sdf2.row_number)
    new_schema = sdf1.join(sdf2,["row_number"])
    print("JOINED PASTE DF")
    #new_schema.show()
    #new_schema.show()
    new_schema=new_schema.drop("row_number")
    return new_schema


In [0]:
from pyspark.ml.evaluation import ClusteringEvaluator
from pyspark.sql.functions import *
from pyspark.sql.window import Window
from pyspark import SparkContext
from pyspark.ml.linalg import Vectors
import pandas as pd

from pyspark.sql.functions import udf
from pyspark.sql.types import *

import math


def getElementFromFeatures(value,idx):
    print(value, idx, value[idx])
    return value[int(idx)]

# NOTE: it seems that calls to udf() must be after SparkContext() is called
udfDistance = udf(getElementFromFeatures, DoubleType())

class covAnomalias:
    
    Pesos=None
    Anomalias=None
        
    def __init__(self, _df, dtCol, _indexCol, niveles):
        self.df = _df
        self.dtCol = dtCol
        self.indexCol = _indexCol
        self.dfk_means = _df 
        self._niveles = niveles
        
        #self._sc = SparkContext.getOrCreate()
        self.limit_distance=3

    '''
    def _get_features(self,df,assembler,scaler):
        print("ANTES DE FEATURES ")
        df.show()
        selectedCols=assembler.getInputCols()+[self.indexCol]
        df=df.select(selectedCols)
        print("GET FEATURES \n", selectedCols,'\n',assembler.getInputCols())
        dfVec=assembler.transform(df)
        print("VECTORIZAR\n")
        print(assembler)
        dfVec.show()        
        dfScaled=scaler.transform(dfVec)    
        print
        #Pasar el campo adecuado a cada modelo
        dfScaled = dfScaled.withColumn('vecFeatures', col('features')).drop('features')
        #KMeans espera una columna 'features'
        dfScaled = dfScaled.withColumn('features', col('scaledFeatures')).drop('scaledFeatures')
        print("Get features")
        dfScaled.show()
        return dfScaled
    '''
    
    def _get_features(self,dfN,assembler,scaler):
        print("ANTES DE FEATURES ")
        dfN.show()
        #df1=dfN.select(self.indexCol)
        #selectedCols=assembler.getInputCols()
        #dfN=dfN.select(selectedCols)
        #print("GET FEATURES \n", selectedCols,'\n',assembler.getInputCols())
        dfVec=assembler.transform(dfN)
        #print("VECTORIZAR\n")
        #print(assembler)
        #dfVec.show()        
        dfScaled=scaler.transform(dfVec)            
        #Pasar el campo adecuado a cada modelo
        dfScaled = dfScaled.withColumn('vecFeatures', col('features')).drop('features')
        #KMeans espera una columna 'features'
        dfScaled = dfScaled.withColumn('features', col('scaledFeatures')).drop('scaledFeatures')
        return dfScaled
    
    def _aplica_modelo_nivel(self, nivel):
        n=nivel
        #print("NIVEL ", n)
        #print(self._niveles[n])
        selectedCols=self._niveles[n]['vars']+[self.indexCol]
        #print("VARIABLES ", self._niveles[n]['vars'])
        dfN=self.df.select(selectedCols)
        #df1=self.df.select(self.indexCol)
        #print("INDEX")
        #df1.show()
        dfN=dfN.drop('features')
        #df=df.drop('features').drop(self.indexCol)
        assembler=self._niveles[n]['assembler']
        scaler=self._niveles[n]['scaler']
        model=self._niveles[n]['kmeans_model']
        #print("Assembler input cols",assembler.getInputCols())
        dfScaled=self._get_features(dfN,assembler,scaler)
        #print("ESCALADO ")
        dfScaled.show()
        dfk_Labeled=model.transform(dfScaled)
        #dfk_Labeled=model.transform(dfScaled.select('features'))
        print("MODELO KMEANS APLICADO")
        print(dfk_Labeled.columns)        
        #print("ANTES DEL PASTE DF")
        #df1.select(self.indexCol).show()        
        #res=self._paste_DF(self.df,dfk_Labeled.select('prediction'))
        res=dfk_Labeled.select(self.indexCol,'prediction','features')
        print("Aplica Modelos Nivel")
        res.show()
        return res

    def _paste_DF(self, sdf1, sdf2): 
        print("PASTE DF ")
        sdf1.show()
        sdf2.show()
        print("Add ROW_NUMBER")
        sdf1 = sdf1.withColumn("row_number", F.row_number().over(Window.partitionBy().orderBy(lit('A'))))
        sdf2 = sdf2.withColumn("row_number", F.row_number().over(Window.partitionBy().orderBy(lit('A'))))        
        sdf1.show()
        sdf2.show()
        #new_schema = sdf1.join(sdf2,sdf1.row_number==sdf2.row_number,'inner').drop(sdf1.row_number).drop(sdf2.row_number)
        new_schema = sdf1.join(sdf2,["row_number"])
        print("JOINED PASTE DF")
        new_schema.show()
        #new_schema.show()
        new_schema=new_schema.drop("row_number")
        return new_schema

    def _anomalies(self, df0, kmModel):
        #Guardo las claves para hacer el DF
        keys=list(df0.select(self.indexCol).toPandas()[self.indexCol])
        #print(type(keys),keys)
        centers = kmModel.clusterCenters()
        #print(centers)
        def distFromCenter(features, c, centers):
            return Vectors.dense(centers[c]).squared_distance(Vectors.dense(features))
        distancias = df0.select("features", "prediction").rdd.map(lambda row: distFromCenter(row.features, row.prediction, centers)).collect()
        #Seleccionamos los puntos anómalos en función de las distancias al centroide
        import math
        #Pasamos una lista a un dataframe en spark
        #print("DISTANCIAS", distancias)
        from pyspark import SparkContext
        sc = SparkContext.getOrCreate()
        lista = sc.parallelize(distancias)
        #print(distancias)
        stats = lista.stats()
        stddev = math.sqrt(stats.variance())
        print("STATS ", stats.mean(), stddev)
        
        outliers = lista.map(lambda x: ("Normal" if (math.fabs(x - stats.mean()) < 3 * stddev) else "Outlier")).collect()
        #print(type(outliers),outliers)
        #df = df.withColumn('Anomalia', lit(''))
        #oo = spark.createDataFrame(outliers)
        
        oo  = spark.createDataFrame(pd.DataFrame(list(zip(keys,outliers,distancias)),columns=[self.indexCol,'outliers','distance']))
        oo.show()
                                    
        return oo

    def _anomaly_fields(self,dfk,dflabels,niv):
      #print(dfk.columns)
      #print(dflabels.columns)
      '''
      if dflabels.filter(col('outliers')=='outlier').count()==0:
        return spark.createDataFrame()
      '''
      dfk=dfk.join(dflabels,[self.indexCol]).drop("features")
      dfk=dfk.withColumn("AnomalyFields",lit(""))
      #dfk.apply(lambda x:{})
      def srtDictAnomaly(variable,value,distance):
          da="{'field':'"+variable+"','value':"+str(value)+",'distance':"+str(distance)+"}"
          return da
      def appendDictAnomaly(d1,d2):
          if len(d1)>0: 
              da=d1+','+d2
          else:
              da=d2
          return da

      def ordenar_anomalias(row):
          #misAnomalias=[]
          #dfrow=pd.DataFrame([row])
          #print('Ordenar anomalias', dfrow) 
          #print("ROW ",row)
          l = ast.literal_eval(row)            
          '''
          if row!="[]": 
              print("ordenar anomalias ", l)
          '''
          if len(l)>0:
              dfd=pd.DataFrame().from_dict(l)
              print(dfd)
              dfd['distance']=dfd['distance'].astype(float)
              dfd['distance']=dfd['distance'].apply(lambda x:math.fabs(x))
              #print("DFD origen", dfd)            
              dfd=dfd.sort_values(['distance'],ascending=False)
              #print("DFD ordendo", dfd)
              #print(dfd[:3])
              #9anomalyRow=pd.DataFrame()
              dfd=dfd[:3]
              #print(dfd.to_dict(orient='records'))
              return dfd.to_dict(orient='records')
          else:
              return []

      def get_element(l,k): 
          try:
              #print(l,k,l[k])
              return l[k]
          except:
              return ""

      #Obtener la lista de clusters
      cluster_list = list(dfk.select('prediction').distinct().toPandas()['prediction'])
      print("NIVEL, CLUSTER_LIST",niv,cluster_list)
      for c in cluster_list:
          ass=self._niveles[niv]['clusters_stats'][c]['assembler']
          scal=self._niveles[niv]['clusters_stats'][c]['scaler']          
          print(c,ass,scal)
          cl = dfk.filter(col('prediction')==c)
          #cl.groupBy().avg().show()
          #cl.show()
          vars = ass.getInputCols()
          #print("ESTAS COLUMNAS TENGO", vars)
          #print("DISTANCIAS", distancias)
          #dicClus
          minidfAss=ass.transform(cl)
          minidf=scal.transform(minidfAss)
          #minidf.select('features','scaledfeatures').show()
          for va, i in zip(vars,range(len(vars))):
              print(va, i)
              '''
              #minidf=minidf.withColumn('distance',udfDistance('scaledfeatures',lit(i)))
              #minidf=minidf.withColumn('distance',col('scaledfeatures')[i])
              minidf.createOrReplaceTempView("df")
              minidf = spark.sql("SELECT "+va+", scaledfeatures, scaledfeatures["+str(i)+"] FROM df")              
              print("SPARK VERSION")
              minidf.show()
              '''
              distances=minidf.select(self.indexCol,va,'scaledFeatures',"AnomalyFields","outliers").toPandas()
              distances['scaledValue']=distances['scaledFeatures'].apply(lambda x:x[i])
              print("VALORES\n",distances)
              distances['outlierField'] = distances['scaledValue'].apply(lambda x: "normal" if (math.fabs(x) < 3) else "outlier")
              print("DISTANCIAS",distances)
              #print(outliers)
              #dfk = pd.concat([dfk,minidf],axis=1)
              #print(dfk.columns)
              #print("AN3      ", an3.columns)
              distances['AnomalyFields'] = distances.apply(lambda x: appendDictAnomaly(x['AnomalyFields'],srtDictAnomaly(va,x[va],x['scaledValue']))  if  x['outlierField']=='outlier'  else x['AnomalyFields'] ,axis=1)
              if len(distances[distances['outlierField']=='outlier'])>0:
                  print(distances[distances['outlierField']=='outlier'][[va,'outlierField','AnomalyFields']])
              distances=distances.drop(['outlierField','scaledValue'],axis=1)
          #Unir con el resto de clusters
          try:
              dfk_tmp=pd.concat([dfk_tmp,distances])
          except:
              dfk_tmp=distances
          
      #print(dfk.columns)
      dfk_tmp['AnomalyFields']=dfk_tmp.apply(lambda x:'' if x['outliers']=='Normal' else x['AnomalyFields'],axis=1)      
      dfk_tmp['AnomalyFields']=dfk_tmp['AnomalyFields'].apply(lambda x: '['+x+']')
      #print(dfk_tmp['AnomalyFields'])      
      dfk_tmp['AnomaliasOrdenadas']=dfk_tmp['AnomalyFields'].apply(lambda row:ordenar_anomalias(row))    
      #print("aNOMALIAS ORDENADAS: ",dfk_tmp['AnomaliasOrdenadas'])
      print("OBTENER ANOMALIAS SEPARADAS:")
      #dfk_tmp['AnomaliasOrdenadas'].apply(lambda x:print(type(x)))
      for field in range(3):
          dfk_tmp['AnomalyField_'+str(field)]=dfk_tmp['AnomaliasOrdenadas'].apply(lambda x:get_element(x,field))
          #dfk_tmp['AnomalyField_'+str(field)].apply(lambda x:print(type(x),x))
          dfk_tmp['Anomaly_'+str(field)]=dfk_tmp['AnomalyField_'+str(field)].apply(lambda x:x['field'] if type(x)==dict else '')
          dfk_tmp['Value_'+str(field)]=dfk_tmp['AnomalyField_'+str(field)].apply(lambda x:str(x['value']) if type(x)==dict else '')
          dfk_tmp['Distance_'+str(field)]=dfk_tmp['AnomalyField_'+str(field)].apply(lambda x:str(x['distance']) if type(x)==dict else '')
          dfk_tmp=dfk_tmp.drop(['AnomalyField_'+str(field)],axis=1)
      dfk_tmp=dfk_tmp.drop(['AnomaliasOrdenadas'],axis=1)
      resCols=[self.indexCol] +  ['Anomaly_0', 'Value_0', 'Distance_0', 'Anomaly_1', 'Value_1', 'Distance_1','Anomaly_2', 'Value_2', 'Distance_2']
      dfk_tmp=dfk_tmp[resCols]
      df=spark.createDataFrame(dfk_tmp)
      dfk=dfk.join(df,[self.indexCol])
      #dfk.show()
      return dfk.select(resCols)

    def renombrar_Anomalias(self,df,niv):
      anomalyCols=["AnomalyFields", 'Anomaly_0', 'Value_0', 'Distance_0', 'Anomaly_1', 'Value_1', 'Distance_1','Anomaly_2', 'Value_2', 'Distance_2']
      for c in df.columns:
          if c in anomalyCols:
            df=df.withColumnRenamed(c,"_".join(["Niv",str(niv),c]))
      return df
      

    def calculaAnomalias(self):
        dfkWithAnomalies=self.df.select(self.indexCol)
        sel=[self.indexCol,'prediction']
        nivList=[]
        for niv in self._niveles.keys():
            if type(niv)==str: continue
            #print(self._niveles[niv])
            '''
            collected = gc.collect()
            print ("Garbage collector: collected %d objects." % collected)
            '''
            sNiv=str(niv)
            print("NIVEL ",sNiv)
            #Obtener la configuracion del niveL: variables, assembler, scaler, kMeans
            dfkLabeled=self._aplica_modelo_nivel(niv)
            print(f"MODELO APLICADO NIVEL {sNiv}")
            print(dfkLabeled.columns)
            #dfkLabeled.show()
            
            model=self._niveles[niv]['kmeans_model']
            print("ENCONTRAR ANOMALIAS")
            dfkOutliers=self._anomalies(dfkLabeled,model)
            
            dfAnomalies=dfkLabeled.join(dfkOutliers,[self.indexCol])
            print("ENCONTRAR CAMPOS RESPONSABLES ANOMALÍA")
            dfAnomalies.show()
            dfAF=self._anomaly_fields(self.df,dfAnomalies,niv)  
            dfAF=self.renombrar_Anomalias(dfAF,niv)
            print("ANOMALY FIELDS COLUMNS",dfAF.columns)
                      
            dfkOutliers=dfkOutliers.withColumnRenamed("outliers","outliers_"+str(niv))
            dfkOutliers=dfkOutliers.withColumnRenamed("distance","distance_"+str(niv))
            
            #dfkOutliers.show()
            colNivel='nivel_'+str(niv)
            dfkLabeled=dfkLabeled.withColumn(colNivel,col('prediction')).drop('prediction')    
            print("ANTES DE JUNTARLO TODO")
            print("APLICAR NIVEL ",dfkLabeled.columns)
            print("Outliers ",dfkOutliers.columns)
            print("ANOMALIAS ",dfAF.columns)            
            dfkWithAnomalies=dfkWithAnomalies.join(dfkLabeled,[self.indexCol]).join(dfkOutliers,[self.indexCol]).drop('features').join(dfAF,[self.indexCol])

            '''
            #print("ANTES DEL PASTE")
            dfkWithAnomalies.show()
            dfkWithAnomalies=paste_DF(dfkWithAnomalies,dfkLabeled.drop('prediction'))
            #dfkLabeled.show()
            print("RESULTADO DEL PASTE")
            dfkWithAnomalies.show()
            '''
            '''
            dfkLabeled=dfkLabeled.select(sel).join(dfkOutliers,[self.indexCol])
            dfkLabeled=dfkLabeled.withColumnRenamed('prediction','cluster_'+str(niv))
            dfkWithAnomalies=dfkWithAnomalies.join(dfkLabeled,[self.indexCol])
            
            dfkWithAnomalies.show()
            '''
            nivList.append(colNivel)
            print("FIN NIVEL ",sNiv)
            
        
        #showCols=[self.indexCol]+[c for c in dfkLabeled.columns if 'nivel_' in c]
        #dfkLabeled.select(showCols).show()
        dfkWithAnomalies=dfkWithAnomalies.withColumn('group',concat_ws('_',*nivList))
        self.anomalias=dfkWithAnomalies
        dfkWithAnomalies.show()

           
        

In [0]:
df_k.select(indexCol,'eth_addr').show()
testingDF=spark.createDataFrame(df_k.toPandas())
testingDF.select(indexCol).show()

+---+--------+
_c0|eth_addr|
+---+--------+
 1| 7.0|
 2| 7.0|
 3| 7.0|
 4| 7.0|
 5| 7.0|
 6| 7.0|
 7| 7.0|
 8| 7.0|
 9| 3.0|
 10| 3.0|
 11| 3.0|
 12| 3.0|
 13| 3.0|
 14| 3.0|
 15| 0.0|
 16| 8.0|
 17| 12.0|
 18| 12.0|
 19| 12.0|
 20| 4.0|
+---+--------+
only showing top 20 rows

+---+
_c0|
+---+
 1|
 2|
 3|
 4|
 5|
 6|
 7|
 8|
 9|
 10|
 11|
 12|
 13|
 14|
 15|
 16|
 17|
 18|
 19|
 20|
+---+
only showing top 20 rows

In [0]:
#an1 = covAnomalias(df_k,'PGG_HASH_INDEX','cosine','cosine',tc1.Niveles)
dft5=testingDF
dft5.select(indexCol).show()
an1 = covAnomalias(df_k,dtCol,indexCol,redecJerarquia)
an1.calculaAnomalias()

+---+
_c0|
+---+
 1|
 2|
 3|
 4|
 5|
 6|
 7|
 8|
 9|
 10|
 11|
 12|
 13|
 14|
 15|
 16|
 17|
 18|
 19|
 20|
+---+
only showing top 20 rows

NIVEL 0
ANTES DE FEATURES 
+---+--------+-----------+---+
_c0|eth_type|ip_src_host|_c0|
+---+--------+-----------+---+
 1| 1.0| 6.0| 1|
 2| 1.0| 6.0| 2|
 3| 1.0| 6.0| 3|
 4| 1.0| 6.0| 4|
 5| 1.0| 6.0| 5|
 6| 1.0| 6.0| 6|
 7| 1.0| 6.0| 7|
 8| 1.0| 6.0| 8|
 9| 2.0| 6.0| 9|
 10| 2.0| 6.0| 10|
 11| 2.0| 6.0| 11|
 12| 2.0| 6.0| 12|
 13| 2.0| 6.0| 13|
 14| 2.0| 6.0| 14|
 15| 0.0| 0.0| 15|
 16| 0.0| 4.0| 16|
 17| 4.0| 6.0| 17|
 18| 4.0| 6.0| 18|
 19| 4.0| 6.0| 19|
 20| 0.0| 2.0| 20|
+---+--------+-----------+---+
only showing top 20 rows

+---+--------+-----------+---+-----------+--------------------+
_c0|eth_type|ip_src_host|_c0|vecFeatures| features|
+---+--------+-----------+---+-----------+--------------------+
 1| 1.0| 6.0| 1| [1.0,6.0]|[-0.0866241673548...|
 2| 1.0| 6.0| 2| [1.0,6.0]|[-0.0866241673548...|
 3| 1.0| 6.0| 3| [1.0,6.0]|[-0.0866241673548...|
 4| 1.0| 6.0| 4| [1.0,6.0]|[-0.0866241673548...|
 5| 1.0| 6.0| 5| [1.0,6.0]|[-0.0866241673548...|
 6| 1.0| 6.0| 6| [1.0,6.0]|[-0.0866241673548...|
 7| 1.0| 6.0| 7| [1.0,6.0]|[-0.0866241673548...|
 8| 1.0| 6.0| 8| [1.0,6.0]|[-0.0866241673548...|
 9| 2.0| 6.0| 9| [2.0,6.0]|[0.85524721235938...|
 10| 2.0| 6.0| 10| [2.0,6.0]|[0.85524721235938...|
 11| 2.0| 6.0| 11| [2.0,6.0]|[0.85524721235938...|
 12| 2.0| 6.0| 12| [2.0,6.0]|[0.85524721235938...|
 13| 2.0| 6.0| 13| [2.0,6.0]|[0.85524721235938...|
 14| 2.0| 6.0| 14| [2.0,6.0]|[0.85524721235938...|
 15| 0.0| 0.0| 15| (2,[],[])|[-1.0284955470690...|
 16| 0.0| 4.0| 16| [0.0,4.0]|[-1.0284955470690...|
 17| 4.0| 6.0| 17| [4.0,6.0]|[2.73898997178778...|
 18| 4.0| 6.0| 18| [4.0,6.0]|[2.73898997178778...|
 19| 4.0| 6.0| 19| [4.0,6.0]|[2.73898997178778...|
 20| 0.0| 2.0| 20| [0.0,2.0]|[-1.0284955470690...|
+---+--------+-----------+---+-----------+--------------------+
only showing top 20 rows

MODELO KMEANS APLICADO
['_c0', 'eth_type', 'ip_src_host', '_c0', 'vecFeatures', 'features', 'prediction']
Aplica Modelos Nivel
+---+----------+--------------------+
_c0|prediction| features|
+---+----------+--------------------+
 1| 0|[-0.0866241673548...|
 2| 0|[-0.0866241673548...|
 3| 0|[-0.0866241673548...|
 4| 0|[-0.0866241673548...|
 5| 0|[-0.0866241673548...|
 6| 0|[-0.0866241673548...|
 7| 0|[-0.0866241673548...|
 8| 0|[-0.0866241673548...|
 9| 5|[0.85524721235938...|
 10| 5|[0.85524721235938...|
 11| 5|[0.85524721235938...|
 12| 5|[0.85524721235938...|
 13| 5|[0.85524721235938...|
 14| 5|[0.85524721235938...|
 15| 1|[-1.0284955470690...|
 16| 6|[-1.0284955470690...|
 17| 10|[2.73898997178778...|
 18| 10|[2.73898997178778...|
 19| 10|[2.73898997178778...|
 20| 2|[-1.0284955470690...|
+---+----------+--------------------+
only showing top 20 rows

MODELO APLICADO NIVEL 0
['_c0', 'prediction', 'features']
ENCONTRAR ANOMALIAS
STATS 0.0005196005813652607 0.00842294042640395
+---+--------+--------------------+
_c0|outliers| distance|
+---+--------+--------------------+
 1| Normal|2.951420232225385...|
 2| Normal|2.951420232225385...|
 3| Normal|2.951420232225385...|
 4| Normal|2.951420232225385...|
 5| Normal|2.951420232225385...|
 6| Normal|2.951420232225385...|
 7| Normal|2.951420232225385...|
 8| Normal|2.951420232225385...|
 9| Normal|1.375083165413376...|
 10| Normal|1.375083165413376...|
 11| Normal|1.375083165413376...|
 12| Normal|1.375083165413376...|
 13| Normal|1.375083165413376...|
 14| Normal|1.375083165413376...|
 15| Normal|1.542469588739959...|
 16| Normal|0.003559972948233404|
 17| Normal|1.972152263052529...|
 18| Normal|1.972152263052529...|
 19| Normal|1.972152263052529...|
 20| Normal|2.007651003787475...|
+---+--------+--------------------+
only showing top 20 rows

ENCONTRAR CAMPOS RESPONSABLES ANOMALÍA
+---+----------+--------------------+--------+--------------------+
_c0|prediction| features|outliers| distance|
+---+----------+--------------------+--------+--------------------+
 1| 0|[-

In [0]:
print(an1.anomalias.columns)
an1.anomalias.select('Niv_0_Distance_0','Niv_0_Anomaly_0', 'Niv_0_Value_0').sort('Niv_0_Distance_0',ascending=False).show(5)
an1.anomalias.sort('Niv_0_Distance_0',ascending=False).show(20)
an1.anomalias.select('Niv_0_Distance_0').show(20)

['_c0', 'nivel_0', 'outliers_0', 'distance_0', 'Niv_0_Anomaly_0', 'Niv_0_Value_0', 'Niv_0_Distance_0', 'Niv_0_Anomaly_1', 'Niv_0_Value_1', 'Niv_0_Distance_1', 'Niv_0_Anomaly_2', 'Niv_0_Value_2', 'Niv_0_Distance_2', 'nivel_1', 'outliers_1', 'distance_1', 'Niv_1_Anomaly_0', 'Niv_1_Value_0', 'Niv_1_Distance_0', 'Niv_1_Anomaly_1', 'Niv_1_Value_1', 'Niv_1_Distance_1', 'Niv_1_Anomaly_2', 'Niv_1_Value_2', 'Niv_1_Distance_2', 'nivel_2', 'outliers_2', 'distance_2', 'Niv_2_Anomaly_0', 'Niv_2_Value_0', 'Niv_2_Distance_0', 'Niv_2_Anomaly_1', 'Niv_2_Value_1', 'Niv_2_Distance_1', 'Niv_2_Anomaly_2', 'Niv_2_Value_2', 'Niv_2_Distance_2', 'nivel_3', 'outliers_3', 'distance_3', 'Niv_3_Anomaly_0', 'Niv_3_Value_0', 'Niv_3_Distance_0', 'Niv_3_Anomaly_1', 'Niv_3_Value_1', 'Niv_3_Distance_1', 'Niv_3_Anomaly_2', 'Niv_3_Value_2', 'Niv_3_Distance_2', 'group']
+----------------+---------------+-------------+
Niv_0_Distance_0|Niv_0_Anomaly_0|Niv_0_Value_0|
+----------------+---------------+-------------+
 | | |
 | | |
 | | |
 | | |
 | | |
+----------------+---------------+-------------+
only showing top 5 rows

+------+-------+----------+--------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+-------+----------+--------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+-------+----------+--------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+-------+----------+------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+--------+
 _c0|nivel_0|outliers_0| distance_0|Niv_0_Anomaly_0|Niv_0_Value_0|Niv_0_Distance_0|Niv_0_Anomaly_1|Niv_0_Value_1|Niv_0_Distance_1|Niv_0_Anomaly_2|Niv_0_Value_2|Niv_0_Distance_2|nivel_1|outliers_1| distance_1|Niv_1_Anomaly_0|Niv_1_Value_0|Niv_1_Distance_0|Niv_1_Anomaly_1|Niv_1_Value_1|Niv_1_Distance_1|Niv_1_Anomaly_2|Niv_1_Value_2|Niv_1_Distance_2|nivel_2|outliers_2| distance_2|Niv_2_Anomaly_0|Niv_2_Value_0|Niv_2_Distance_0|Niv_2_Anomaly_1|Niv_2_Value_1|Niv_2_Distance_1|Niv_2_Anomaly_2|Niv_2_Value_2|Niv_2_Distance_2|nivel_3|outliers_3| distance_3|Niv_3_Anomaly_0|Niv_3_Value_0|Niv_3_Distance_0|Niv_3_Anomaly_1|Niv_3_Value_1|Niv_3_Distance_1|Niv_3_Anomaly_2|Niv_3_Value_2|Niv_3_Distance_2| group|
+------+-------+----------+--------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+-------+----------+--------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+-------+----------+--------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+-------+----------+------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+--------+
245074| 5| Normal|1.375083165413376...| | | | | | | | | | 0| Normal| 0.2769634875726856| | | | | | | | | | 10| Normal| 0.23458979639446376| | | | | | | | | | 0| Normal|1.0877683247905612| | | | | | | | | |5_0_10_0|
245123| 8| Normal|2.991754983050687...| | | | | | | | | | 1| Normal| 0.7590798454275042| | | | | | | | | | 5| Normal| 0.5842481086328939| | | | | | | | | | 0| Normal|1.3330106840255964| | | | | | | | | | 8_1_5_0|
245390| 3| Normal|4.452750031423289...| | | | | | | | | | 2| Normal| 0.3031378727492125| | | | | | | | | | 8| Normal| 1.9294939598028737| | | | | | | | | | 1| Normal| 2.470349382619557| | | | | | | | | | 3_2_8_1|
245534| 2| Normal|2.007651003787475...| | | | | | | | | | 1| Normal| 0.9715335

In [0]:
anomalias= an1.anomalias

try:
    spark.sql(f"drop table ClasificacionNiveles{sufijo}")
except:
    print(f"No existe la tabla ClasificacionNiveles{sufijo}")

anomalias.createOrReplaceTempView("mytempTable")
spark.sql(f"create table ClasificacionNiveles{sufijo} as select * from mytempTable")


Out[43]: DataFrame[]

In [0]:
print(modelsPath)
try:
  os.chdir(os.path.join(modelsPath,"results"))
except:
  os.mkdir(os.path.join(modelsPath,"results"))
  os.chdir(os.path.join(modelsPath,"results"))

an1.anomalias.toPandas().to_csv(os.path.join(modelsPath,"results",f"redec_anomalies{sufijo}.csv"))

/dbfs/FileStore/redec/tecnalia_2021

In [0]:
oc=[c for c in an1.anomalias.columns if 'outl' in c]+[indexCol]
an1.anomalias.select(oc).sort(oc,ascending=False).show()
n0=[c for c in an1.anomalias.columns if c.endswith("_0")]+[indexCol]
an1.anomalias.select(n0).sort(n0,ascending=False).show()

+----------+----------+----------+----------+------+
outliers_0|outliers_1|outliers_2|outliers_3| _c0|
+----------+----------+----------+----------+------+
 Outlier| Outlier| Outlier| Outlier|250342|
 Outlier| Outlier| Outlier| Outlier|250341|
 Outlier| Outlier| Outlier| Outlier|250340|
 Outlier| Outlier| Outlier| Outlier|249641|
 Outlier| Outlier| Outlier| Outlier|249640|
 Outlier| Outlier| Outlier| Outlier|249639|
 Outlier| Outlier| Outlier| Outlier|248462|
 Outlier| Outlier| Outlier| Outlier|248461|
 Outlier| Outlier| Outlier| Outlier|248460|
 Outlier| Outlier| Outlier| Outlier|247277|
 Outlier| Outlier| Outlier| Outlier|247276|
 Outlier| Outlier| Outlier| Outlier|247275|
 Outlier| Outlier| Outlier| Outlier|246083|
 Outlier| Outlier| Outlier| Outlier|246082|
 Outlier| Outlier| Outlier| Outlier|246081|
 Outlier| Outlier| Outlier| Outlier|245558|
 Outlier| Outlier| Outlier| Outlier|245557|
 Outlier| Outlier| Outlier| Outlier|245556|
 Outlier| Outlier| Outlier| Outlier|244875|
 Outlier| Outlier| Outlier| Outlier|244874|
+----------+----------+----------+----------+------+
only showing top 20 rows

+-------+----------+--------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+------+
nivel_0|outliers_0| distance_0|Niv_0_Anomaly_0|Niv_0_Value_0|Niv_0_Distance_0|Niv_1_Anomaly_0|Niv_1_Value_0|Niv_1_Distance_0|Niv_2_Anomaly_0|Niv_2_Value_0|Niv_2_Distance_0|Niv_3_Anomaly_0|Niv_3_Value_0|Niv_3_Distance_0| _c0|
+-------+----------+--------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+------+
 10| Normal|1.972152263052529...| | | | | | | | | | | | |248511|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |248510|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |248509|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |248508|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |248352|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |248351|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |248350|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |246418|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |246417|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |246416|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |246415|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |246253|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |246252|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |246251|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |244278|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |244277|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |244276|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |244275|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |244152|
 10| Normal|1.972152263052529...| | | | | | | | | | | | |244151|
+-------+----------+--------------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+---------------+-------------+----------------+------+
only showing top 20 rows

In [0]:
redecJerarquia

Out[46]: {0: {'vars': ['_c0', 'eth_type', 'ip_src_host'],
 'assembler': VectorAssembler_95fc1fc40eae,
 'scaler': StandardScalerModel: uid=StandardScaler_413dc017da71, numFeatures=2, withMean=true, withStd=true,
 'kmeans_model': KMeansModel: uid=KMeans_a2a196867321, k=11, distanceMeasure=euclidean, numFeatures=2,
 'clusters_stats': {1: {'assembler': VectorAssembler_da8b9294e3d1,
 'scaler': StandardScalerModel: uid=StandardScaler_16488065b42c, numFeatures=2, withMean=true, withStd=true},
 6: {'assembler': VectorAssembler_a4611e260673,
 'scaler': StandardScalerModel: uid=StandardScaler_d79466d8826d, numFeatures=2, withMean=true, withStd=true},
 3: {'assembler': VectorAssembler_613f39a37720,
 'scaler': StandardScalerModel: uid=StandardScaler_c4f732e702f7, numFeatures=2, withMean=true, withStd=true},
 5: {'assembler': VectorAssembler_9ac84f1dc105,
 'scaler': StandardScalerModel: uid=StandardScaler_add6f4760f1c, numFeatures=2, withMean=true, withStd=true},
 9: {'assembler': VectorAssembler_a700320ba469,
 'scaler': StandardScalerModel: uid=StandardScaler_e9e495e8131c, numFeatures=2, withMean=true, withStd=true},
 4: {'assembler': VectorAssembler_7c83b4f04332,
 'scaler': StandardScalerModel: uid=StandardScaler_283f3d364d7b, numFeatures=2, withMean=true, withStd=true},
 8: {'assembler': VectorAssembler_54199415c00c,
 'scaler': StandardScalerModel: uid=StandardScaler_f8ec95427730, numFeatures=2, withMean=true, withStd=true},
 7: {'assembler': VectorAssembler_08b7759b4ce4,
 'scaler': StandardScalerModel: uid=StandardScaler_2d001e36965a, numFeatures=2, withMean=true, withStd=true},
 10: {'assembler': VectorAssembler_fc4ede3915b3,
 'scaler': StandardScalerModel: uid=StandardScaler_f654ff7606e1, numFeatures=2, withMean=true, withStd=true},
 2: {'assembler': VectorAssembler_993e0e4e5789,
 'scaler': StandardScalerModel: uid=StandardScaler_8a2547289d4c, numFeatures=2, withMean=true, withStd=true},
 0: {'assembler': VectorAssembler_555118b84d05,
 'scaler': StandardScalerModel: uid=StandardScaler_8c0a29a5522e, numFeatures=2, withMean=true, withStd=true}}},
 1: {'vars': ['_c0',
 'eth_src_resolved',
 'frame_cap_len',
 'ip_len',
 'tcp_len',
 'tcp_seq_raw',
 'tcp_window_size',
 'tcp_window_size_scalefactor'],
 'assembler': VectorAssembler_7fa13bcf2b57,
 'scaler': StandardScalerModel: uid=StandardScaler_bb5817926366, numFeatures=7, withMean=true, withStd=true,
 'kmeans_model': KMeansModel: uid=KMeans_f16919a778e8, k=4, distanceMeasure=euclidean, numFeatures=7,
 'clusters_stats': {1: {'assembler': VectorAssembler_48f5fc893479,
 'scaler': StandardScalerModel: uid=StandardScaler_3e2c70fcb4df, numFeatures=7, withMean=true, withStd=true},
 3: {'assembler': VectorAssembler_590473ce038d,
 'scaler': StandardScalerModel: uid=StandardScaler_c17ee3e6e54c, numFeatures=7, withMean=true, withStd=true},
 2: {'assembler': VectorAssembler_6a7d4afaa629,
 'scaler': StandardScalerModel: uid=StandardScaler_e90885a13924, numFeatures=7, withMean=true, withStd=true},
 0: {'assembler': VectorAssembler_8718d0636f02,
 'scaler': StandardScalerModel: uid=StandardScaler_27ab5cc22866, numFeatures=7, withMean=true, withStd=true}}},
 2: {'vars': ['_c0',
 'eth_addr_resolved',
 'eth_dst',
 'eth_padding',
 'eth_src',
 'frame_len',
 'tcp_analysis',
 'tcp_port',
 'tcp_seq'],
 'assembler': VectorAssembler_74d2889fa262,
 'scaler': StandardScalerModel: uid=StandardScaler_2ff2f64ff50c, numFeatures=8, withMean=true, withStd=true,
 'kmeans_model': KMeansModel: uid=KMeans_81376704e3fe, k=12, distanceMeasure=euclidean, numFeatures=8,
 'clusters_stats': {1: {'assembler': VectorAssembler_1301ba1d32c4,
 'scaler': StandardScalerModel: uid=StandardScaler_e094326785a9, numFeatures=8, withMean=true, withStd=true},
 6: {'assembler': VectorAssembler_f306f4594abe,
 'scaler': StandardScalerModel: uid=StandardScaler_253ee66e33c9, numFeatures=8, withMean=true, withStd=true},
 3: {'assembler': VectorAssembler_e3787954276e,
 'scaler': StandardScalerModel: uid=StandardScaler_7ef386eebf49, numFeatures=8, withMea

In [0]:
fname=f"redecGroupCenter{sufijo}.dct"
fname=os.path.join(modelsPath,fname)

f=open(fname,"r")
CenterGroup=f.read()
f.close()

dctCenterGroup=ast.literal_eval(CenterGroup)

print(dctCenterGroup)


{'0_0_0_0': 0.0, '0_0_0_1': 0.0, '0_0_1_0': 0.0, '0_0_1_1': 0.0, '0_0_2_0': 0.0, '0_0_2_1': 0.0, '0_0_3_0': 0.14978015790293403, '0_0_3_1': 0.0, '0_0_4_0': 0.0, '0_0_4_1': 0.0, '0_0_5_0': 0.0, '0_0_5_1': 0.0, '0_0_6_0': 0.0, '0_0_6_1': 0.0, '0_0_7_0': 0.11430590997855491, '0_0_7_1': 0.0, '0_0_8_0': 0.0, '0_0_8_1': 0.0, '0_0_9_0': 0.0, '0_0_9_1': 0.0, '0_0_10_0': 0.028753189806994213, '0_0_10_1': 0.0, '0_0_11_0': 0.0, '0_0_11_1': 0.0, '0_1_0_0': 0.0, '0_1_0_1': 0.0, '0_1_1_0': 0.0, '0_1_1_1': 0.0, '0_1_2_0': 0.0, '0_1_2_1': 0.0, '0_1_3_0': 0.0, '0_1_3_1': 0.0, '0_1_4_0': 0.0, '0_1_4_1': 0.0, '0_1_5_0': 0.0, '0_1_5_1': 0.0, '0_1_6_0': 0.0, '0_1_6_1': 0.0, '0_1_7_0': 0.0, '0_1_7_1': 0.0, '0_1_8_0': 0.0, '0_1_8_1': 0.0, '0_1_9_0': 0.0, '0_1_9_1': 0.0, '0_1_10_0': 0.0, '0_1_10_1': 0.0, '0_1_11_0': 0.0, '0_1_11_1': 0.0, '0_2_0_0': 0.0, '0_2_0_1': 0.0, '0_2_1_0': 0.0, '0_2_1_1': 0.0, '0_2_2_0': 0.0, '0_2_2_1': 0.0, '0_2_3_0': 0.0, '0_2_3_1': 0.0, '0_2_4_0': 0.0, '0_2_4_1': 0.0, '0_2_5_0': 0.0, '0_2_5_1': 0.0, '0_2_6_0': 0.0, '0_2_6_1': 0.0, '0_2_7_0': 0.0, '0_2_7_1': 0.0, '0_2_8_0': 0.0, '0_2_8_1': 0.05737858765929067, '0_2_9_0': 0.0, '0_2_9_1': 0.0, '0_2_10_0': 0.0, '0_2_10_1': 0.0, '0_2_11_0': 0.0, '0_2_11_1': 0.0, '0_3_0_0': 0.0, '0_3_0_1': 0.0, '0_3_1_0': 0.0, '0_3_1_1': 0.0, '0_3_2_0': 0.0, '0_3_2_1': 0.0, '0_3_3_0': 0.0, '0_3_3_1': 0.0, '0_3_4_0': 0.0, '0_3_4_1': 0.0, '0_3_5_0': 0.0, '0_3_5_1': 0.0, '0_3_6_0': 0.0, '0_3_6_1': 0.0, '0_3_7_0': 0.0, '0_3_7_1': 0.0, '0_3_8_0': 0.0, '0_3_8_1': 0.0, '0_3_9_0': 0.0, '0_3_9_1': 0.0, '0_3_10_0': 0.0, '0_3_10_1': 0.0, '0_3_11_0': 0.0, '0_3_11_1': 0.0, '1_0_0_0': 0.001916879320466281, '1_0_0_1': 1.597399433721901e-05, '1_0_1_0': 0.0, '1_0_1_1': 0.0, '1_0_2_0': 0.0, '1_0_2_1': 0.0, '1_0_3_0': 0.0, '1_0_3_1': 0.0, '1_0_4_0': 0.0, '1_0_4_1': 0.0, '1_0_5_0': 0.0, '1_0_5_1': 0.0, '1_0_6_0': 0.0, '1_0_6_1': 0.0, '1_0_7_0': 0.0, '1_0_7_1': 0.0, '1_0_8_0': 0.0, '1_0_8_1': 0.0, '1_0_9_0': 0.0, '1_0_9_1': 0.0, '1_0_10_0': 0.0, '1_0_10_1': 7.986997168609503e-05, '1_0_11_0': 0.0, '1_0_11_1': 0.0, '1_1_0_0': 0.0, '1_1_0_1': 0.0, '1_1_1_0': 0.1174847348516615, '1_1_1_1': 1.1980495752914256e-05, '1_1_2_0': 0.0, '1_1_2_1': 0.0, '1_1_3_0': 0.0, '1_1_3_1': 0.0, '1_1_4_0': 0.0, '1_1_4_1': 0.0, '1_1_5_0': 0.0, '1_1_5_1': 0.0, '1_1_6_0': 0.0, '1_1_6_1': 0.0, '1_1_7_0': 0.0, '1_1_7_1': 0.0, '1_1_8_0': 0.0, '1_1_8_1': 0.0, '1_1_9_0': 0.0, '1_1_9_1': 0.0, '1_1_10_0': 0.0, '1_1_10_1': 0.0, '1_1_11_0': 0.0, '1_1_11_1': 0.0, '1_2_0_0': 0.0, '1_2_0_1': 0.0, '1_2_1_0': 0.0, '1_2_1_1': 0.0, '1_2_2_0': 0.0, '1_2_2_1': 0.0, '1_2_3_0': 0.0, '1_2_3_1': 0.0, '1_2_4_0': 0.0, '1_2_4_1': 0.0, '1_2_5_0': 0.0, '1_2_5_1': 0.0, '1_2_6_0': 0.0, '1_2_6_1': 0.0, '1_2_7_0': 0.0, '1_2_7_1': 0.0, '1_2_8_0': 0.0, '1_2_8_1': 0.0, '1_2_9_0': 0.0, '1_2_9_1': 0.0, '1_2_10_0': 0.0, '1_2_10_1': 0.0, '1_2_11_0': 0.0, '1_2_11_1': 0.0, '1_3_0_0': 0.0, '1_3_0_1': 0.0, '1_3_1_0': 0.0, '1_3_1_1': 0.0, '1_3_2_0': 0.0, '1_3_2_1': 0.0, '1_3_3_0': 0.0, '1_3_3_1': 0.0, '1_3_4_0': 0.0, '1_3_4_1': 0.0, '1_3_5_0': 0.0, '1_3_5_1': 0.0, '1_3_6_0': 0.0, '1_3_6_1': 0.0, '1_3_7_0': 0.0, '1_3_7_1': 0.0, '1_3_8_0': 0.0, '1_3_8_1': 0.0, '1_3_9_0': 0.0, '1_3_9_1': 0.0, '1_3_10_0': 0.0, '1_3_10_1': 0.0, '1_3_11_0': 0.0, '1_3_11_1': 0.0, '2_0_0_0': 0.0, '2_0_0_1': 0.0, '2_0_1_0': 0.0, '2_0_1_1': 0.0, '2_0_2_0': 0.0, '2_0_2_1': 0.0, '2_0_3_0': 0.0, '2_0_3_1': 0.0, '2_0_4_0': 0.0, '2_0_4_1': 0.0, '2_0_5_0': 0.0, '2_0_5_1': 0.0, '2_0_6_0': 0.0, '2_0_6_1': 0.0, '2_0_7_0': 0.0, '2_0_7_1': 0.0, '2_0_8_0': 0.0, '2_0_8_1': 0.0, '2_0_9_0': 0.0, '2_0_9_1': 0.0, '2_0_10_0': 0.0, '2_0_10_1': 0.0, '2_0_11_0': 0.0, '2_0_11_1': 0.0, '2_1_0_0': 0.0, '2_1_0_1': 0.0, '2_1_1_0': 0.0, '2_1_1_1': 0.0, '2_1_2_0': 0.0, '2_1_2_1': 0.0, '2_1_3_0': 0.0, '2_1_3_1': 0.0, '2_1_4_0': 0.0, '2_1_4_1': 0.0, '2_1_5_0': 0.025614299919730677, '2_1_5_1': 0.003578174731537058, '2_1_6_0': 0.0, '2_1_6_1': 0.0, '2_1_7_0': 0.0, '2_1_7_1': 0.0, '2_1_8_0': 0.0, '2_1_8_1': 0.0, '2_1_9_0': 0.002859344986362202, 

In [0]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.linalg import SparseVector, DenseVector
from pyspark.sql import types as T
import numpy as np

class covAnomaliasAgrupado:
  
    def __init__(self, niveles, df, dtCol, indexCol):
        self.df = df
        self.dtCol = dtCol
        self.indexCol = indexCol
        self._niveles= niveles
        dctGroup=redecJerarquia['groups']
        center=dctGroup['center']
        pdCenter=pd.DataFrame([center],columns=dctGroup['vars'])
        self._groupCenter=spark.createDataFrame(pdCenter)
        ass=dctGroup['assembler']
        tmpCenter=ass.transform(self._groupCenter).select('features').rdd.flatMap(lambda x: x).collect()
        scal=dctGroup['scaler']
        self._stdGroup=scal
        self._groupCenterList=[]
        for c in tmpCenter:
            cDense=DenseVector(c)                 
            new_array = list([float(x) for x in cDense])
            self._groupCenterList.append(new_array)
        self._assembler=ass
        self._scaler=scal

    def _aplica_modelos_niveles(self):
        #print(self._niveles)        
        nivList=[]
        dfk_Labeled=self.df
        for n in self._niveles.keys():
            if type(n)==str: continue
            n=int(n)
            print("NIVEL ", n)
            #print(self._niveles[n])
            selectedCols=self._niveles[n]['vars']
            print("VARIABLES ", self._niveles[n]['vars'])
            #df=self.df.select(selectedCols)
            #df1=df.select(self.indexCol)
            dfk_Labeled=dfk_Labeled.drop('features')
            #df=df.drop('features').drop(self.indexCol)
            assembler=self._niveles[n]['assembler']
            scaler=self._niveles[n]['scaler']
            model=self._niveles[n]['kmeans_model']
            #print("iNPUT COLS",assembler.getInputCols())
            '''
            print("COLUMNA DE SALIDA ass",assembler.getInputCols(),assembler.getOutputCol())
            print("SCALER INOUTPUT", scaler.getInputCol(), scaler.getOutputCol())            
            print("MODEL INOUTPUT", model.getFeaturesCol(), model.getPredictionCol())            
            '''
            #df.show()
            print("Vectorizar esto:",dfk_Labeled.columns)
            dfVec=assembler.transform(dfk_Labeled)
            print("COLUMNAS VEC ",dfVec.columns)
            dfVec.select(self.indexCol).show()
            #dfVec.show()
            dfScaled=scaler.transform(dfVec)    
            print("COLUMNAS SCAL ",dfScaled.columns)
            #Pasar el campo adecuado a cada modelo
            dfScaled = dfScaled.withColumn('vecFeatures', col('features')).drop('features')
            #KMeans espera una columna 'features'
            dfScaled = dfScaled.withColumn('features', col('scaledFeatures')).drop('scaledFeatures')  
            dfScaled.select(self.indexCol).show(10)
            print("Scaled")
            #dfScaled.show(10)
            dfk_Labeled=model.transform(dfScaled)
            dfk_Labeled.select('prediction').distinct().show()
            dfk_Labeled.select(self.indexCol).show()
            #Juntar predicciones con features
            #dfk_Labeled=self._paste_DF(df1,dfk_Labeled)
            #Para debug
            '''dfkunir=dfk_Labeled.select(self.indexCol,'features','prediction')
            dfkunir=dfkunir.withColumn('nivel',lit(n))
            print("unir ordenado por indice") 
            dfkunir.sort(self.indexCol).show()
            try:
                self.dfTodo=self.dfTodo.join(dfkunir,on=self.indexCol,how='outer')
                print("Bien unido")
            except:
                self.dfTodo=dfkunir
                print("Nuevo dfTodo")
            #
            print("TODO")
            self.dfTodo.show()
            '''
            colNivel='nivel_'+str(n)
            nivList.append(colNivel)
            dfk_Labeled=dfk_Labeled.withColumnRenamed('prediction',colNivel)
            #dfk_Labeled=dfk_Labeled.select(self.indexCol,colNivel)
            print("LABELED", dfk_Labeled.columns)
            #dfk_Labeled.show()
            '''
            try:
                dfNiveles=dfNiveles.join(dfk_Labeled,on=self.indexCol,how='outer')
            except:
                dfNiveles=dfk_Labeled
            '''

        dfNiveles=dfk_Labeled.withColumn('group',concat_ws('_',*nivList))
        print(dfNiveles)        
        self._dfNiveles=dfNiveles
        
    def _get_All_Combinations(self, df):
        colsGroups=self._groupCenter.columns
        try:
            colsGroups.remove(self.dtCol)
        except:
            colsGroups=colsGroups
        return colsGroups
      
        colsNivel=[c for c in df.columns if c.startswith('nivel_')]
        colsNivel=sorted(colsNivel)
        nivelesList=[]
        for c in colsNivel:
            listaN=sorted(list(df.select(c).sort(c).distinct().toPandas()[c]))
            print(listaN)
            nivelesList.append(listaN)

        result = list(itertools.product(*nivelesList))
        #print(result)
        #str(x) for x in list_of_ints
        allgroups=['_'.join([str(x) for x in g]) for g in result]

        #print(allgroups)
        return allgroups
      
    def _complete_groups(self, df):
        normalGroups=df.columns
        allgroups=self._get_All_Combinations(self._dfNiveles)
                
        contenidos=[f for f in allgroups if f in normalGroups]
        nocontenidos=[f for f in allgroups if f not in normalGroups]   
        
        #print("NOT NORMALES ", nocontenidos)
        dfNO = spark.createDataFrame(
          [
            tuple(0 for i in nocontenidos)
          ],
          nocontenidos
        )        
        dfNO.show()
        '''
        for g in allgroups:
            if g not in normalGroups:
                df=df.withColumn(g, lit(0.0))
        '''
        print(df.count())
        df=df.crossJoin(dfNO)
        selectedCols=[self.dtCol]+allgroups
        print(df.count())        
        #df.show(2)
        print(df.dtypes)
        return df.select(selectedCols)
      
    def _modela_agrupado(self):
        #df_grouped=self._dfNiveles.join(self.df.select(self.indexCol,self.dtCol),[self.indexCol])
        df_grouped=self._dfNiveles
        colsNivel=[c for c in df_grouped.columns if c.startswith('nivel_')]
        df_grouped.groupBy('group').count().sort('group').show()
               
        seq = df_grouped.groupby(self.dtCol).pivot("group").count().sort(self.dtCol)
        #seq.show()
        seq=seq.fillna(0.0)
        print("AGRUPADO ")
        seq.show()
        seq=self._complete_groups(seq)
        self._grouped=seq
        
        seq.show()
    
    def _vectorize(self,df):
        vecCols=df.columns
        for c in [self.dtCol,self.indexCol]:
          try:
              vecCols.remove(c)
          except:
              vecCols=vecCols
        #print("Vectorizar: ", vecCols)
        ass=VectorAssembler(inputCols=vecCols,outputCol='features')
        df=ass.transform(df) 
        #f=list(df.select('features').toPandas()['features'])[:3]
        #print(f)
        #df.select('features').show(2)
        return df
        
    def _anomalies(self, df0, centers):
        print("Busqueda de anomalias")
        dataCols=list(df0.columns)
        dataCols.remove(self.dtCol)
        for c in dataCols:
            df0=df0.withColumn(c,col(c).cast(DoubleType()))
            #print(df0.select(c).dtypes)
            
        @udf(T.ArrayType(T.FloatType()))
        def  toDense(v):
            try:
                v = DenseVector(v)                 
                new_array = list([float(x) for x in v])
            except:
                print("Error en Dense   ", v)
                new_array=[0.0 for x in v]
            return new_array 
          
        if 'features' not in df0.columns:
            df0=self._vectorize(df0)
            print(df0.columns)
        df0=df0.withColumn('features',toDense('features'))
        print(len(centers[0]))
        df0=df0.withColumn('len',size(col('features')))
        df0.select('features','len').show()
        #Guardo las claves para hacer el DF
        keys=list(df0.select(self.dtCol).toPandas()[self.dtCol])
        #print(type(keys),keys)
        print(centers[0], type(centers[0]))
        def distFromCenter(features, centers):            
            return Vectors.dense(centers).squared_distance(Vectors.dense(features))
            #return centers.squared_distance(features)
        distancias = df0.select("features").rdd.map(lambda row: distFromCenter(row.features, centers[0])).collect()
        #Seleccionamos los puntos anómalos en función de las distancias al centroide
        import math
        #Pasamos una lista a un dataframe en spark
        #print("DISTANCIAS", distancias)
        from pyspark import SparkContext
        sc = SparkContext.getOrCreate()
        lista = sc.parallelize(distancias)
        #print(distancias)
        stats = lista.stats()
        stddev = math.sqrt(stats.variance())
        print("STATS ", stats.mean(), stddev)
        
        outliers = lista.map(lambda x: ("Normal" if (math.fabs(x - stats.mean()) < 3 * stddev) else "Outlier")).collect()
        #print(type(outliers),outliers)
        #df = df.withColumn('Anomalia', lit(''))
        #oo = spark.createDataFrame(outliers)
        
        #oo  = spark.createDataFrame(pd.DataFrame(list(zip(keys,distancias,outliers)),columns=[self.dtCol,'distance','outliers']))
        intermedio=pd.DataFrame(list(zip(distancias,outliers)),columns=['distance','outliers'])
        intermedio[dtCol]=keys
        print(intermedio)
        oo  = spark.createDataFrame(intermedio)
        #oo = oo.withColumn
        oo.show()
                                    
        return oo                                                                                                                                                                   

    def _anomaly_fields(self,dfk,dflabels):
    
      dfk=dfk.join(dflabels,[self.dtCol]).drop("features")
      dfk=dfk.withColumn("AnomalyFields",lit(""))
      
      #dfk.apply(lambda x:{})
      def srtDictAnomaly(variable,value,distance):
          da="{'field':'"+variable+"','value':"+str(value)+",'distance':"+str(distance)+"}"
          return da
      def appendDictAnomaly(d1,d2):
          if len(d1)>0: 
              da=d1+','+d2
          else:
              da=d2
          return da

      def ordenar_anomalias(row):
          #misAnomalias=[]
          #dfrow=pd.DataFrame([row])
          #print('Ordenar anomalias', dfrow) 
          print("ROW ",row)
          l = ast.literal_eval(row)            
          '''
          if row!="[]": 
              print("ordenar anomalias ", l)
          '''
          if len(l)>0:
              dfd=pd.DataFrame().from_dict(l)
              print(dfd)
              dfd['distance']=dfd['distance'].astype(float)
              dfd['distance']=dfd['distance'].apply(lambda x:math.fabs(x))
              #print("DFD origen", dfd)            
              dfd=dfd.sort_values(['distance'],ascending=False)
              #print("DFD ordendo", dfd)
              #print(dfd[:3])
              #9anomalyRow=pd.DataFrame()
              dfd=dfd[:3]
              #print(dfd.to_dict(orient='records'))
              return dfd.to_dict(orient='records')
          else:
              return []
            
      def anomaly_fields_pd(row,cols,featuresField):
          fieldDistList=row[featuresField]
          print(type(fieldDistList))
          npFeatures=np.array(fieldDistList)
          posAnomalos=np.argwhere(np.abs(npFeatures)>3)
          totalAF=""
          for pos in posAnomalos:
              var=cols[pos[0]]
              value=row[var]
              distance=npFeatures[pos[0]]
              f=srtDictAnomaly(var,value,distance)
              #print(f)
              totalAF=appendDictAnomaly(totalAF,f)

          #print(totalAF)
          return totalAF

      def get_element(l,k): 
          try:
              #print(l,k,l[k])
              return l[k]
          except:
              return ""

      #Vectorizar y escaler el grupo
      ass=self._assembler
      scal=self._scaler
      #scal.setOutputCol("scaledFeatures")
      vars = ass.getInputCols()
      print(dfk.columns)
      minidfAss=ass.transform(dfk)
      print(minidfAss.columns)
      print(scal.getInputCol(), scal.getOutputCol())
      minidf=scal.transform(minidfAss)
      pdminidf=minidf.toPandas()
      pdminidf['AnomalyFields']=pdminidf.apply(lambda row:anomaly_fields_pd(row,vars,'scaledFeatures'),axis=1)
      

      '''
      print("TONUMPY    ", np.array(minidf.select('features').toPandas()['features'].to_numpy()))
      return
      for va, i in zip(vars,range(len(vars))):
          print(va, i)
          distances=minidf.select(self.dtCol,va,'scaledFeatures',"AnomalyFields","outliers").toPandas()
          distances['scaledValue']=distances['scaledFeatures'].apply(lambda x:x[i])
          #print("VALORES\n",distances)
          distances['outlierField'] = distances['scaledValue'].apply(lambda x: "normal" if (math.fabs(x) < 3) else "outlier")
          #print(outliers)
          #dfk = pd.concat([dfk,minidf],axis=1)
          #print(dfk.columns)
          #print("AN3      ", an3.columns)
          distances['AnomalyFields'] = distances.apply(lambda x: appendDictAnomaly(x['AnomalyFields'],srtDictAnomaly(va,x[va],x['scaledValue']))  if  x['outlierField']=='outlier'  else x['AnomalyFields'] ,axis=1)
          if len(distances[distances['outlierField']=='outlier'])>0:
              print(distances[distances['outlierField']=='outlier'][[va,'outlierField','AnomalyFields']])
          distances=distances.drop(['outlierField','scaledValue'],axis=1)
      '''
      dfk_tmp=pdminidf
      
      
           
      #print(dfk.columns)
      #dfk_tmp['AnomalyFields']=dfk_tmp.apply(lambda x:'' if x['outliers']=='Normal' else x['AnomalyFields'],axis=1)      
      dfk_tmp['AnomalyFields']=dfk_tmp.apply(lambda x:x['AnomalyFields'],axis=1)      
      dfk_tmp['AnomalyFields']=dfk_tmp['AnomalyFields'].apply(lambda x: '['+x+']')
      #print(dfk_tmp['AnomalyFields'])      
      dfk_tmp['AnomaliasOrdenadas']=dfk_tmp['AnomalyFields'].apply(lambda row:ordenar_anomalias(row))    
      #print("aNOMALIAS ORDENADAS: ",dfk_tmp['AnomaliasOrdenadas'])
      print("OBTENER ANOMALIAS SEPARADAS:")
      #dfk_tmp['AnomaliasOrdenadas'].apply(lambda x:print(type(x)))
      for field in range(3):
          dfk_tmp['AnomalyField_'+str(field)]=dfk_tmp['AnomaliasOrdenadas'].apply(lambda x:get_element(x,field))
          #dfk_tmp['AnomalyField_'+str(field)].apply(lambda x:print(type(x),x))
          dfk_tmp['Anomaly_'+str(field)]=dfk_tmp['AnomalyField_'+str(field)].apply(lambda x:x['field'] if type(x)==dict else '')
          dfk_tmp['Value_'+str(field)]=dfk_tmp['AnomalyField_'+str(field)].apply(lambda x:str(x['value']) if type(x)==dict else '')
          dfk_tmp['Distance_'+str(field)]=dfk_tmp['AnomalyField_'+str(field)].apply(lambda x:str(x['distance']) if type(x)==dict else '')
          dfk_tmp=dfk_tmp.drop(['AnomalyField_'+str(field)],axis=1)
      dfk_tmp=dfk_tmp.drop(['AnomaliasOrdenadas'],axis=1)
      resCols=[self.dtCol] +  ['Anomaly_0', 'Value_0', 'Distance_0', 'Anomaly_1', 'Value_1', 'Distance_1','Anomaly_2', 'Value_2', 'Distance_2']
      dfk_tmp=dfk_tmp[resCols]
      df=spark.createDataFrame(dfk_tmp)
      dfk=dfk.join(df,[self.dtCol])
      #dfk.show()
      return dfk.select(resCols)



In [0]:
dft=dfTrain.select(indexCol,dtCol)

dft=dft.join(df_k,[indexCol])


In [0]:
dft.show()


+---+--------------------+-------+--------+----------+---------+---------------------------+------+---------------+-------------+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+
_c0| frame_time_epoch|tcp_len|tcp_port| tcp_seq|frame_len|tcp_window_size_scalefactor|ip_len|tcp_window_size| tcp_seq_raw|vssmonitoring_srcport|frame_cap_len|eth_addr|eth_addr_resolved|eth_dst|eth_dst_resolved|eth_padding|eth_src|eth_src_resolved|eth_type|frame_interface_name|frame_protocols|ip_addr|ip_dsfield|ip_dst|ip_dst_host|ip_flags|ip_host|ip_src|ip_src_host|tcp_analysis|tcp_flags|
+---+--------------------+-------+--------+----------+---------+---------------------------+------+---------------+-------------+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+
 1|1.6214274714668849E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 2|1.6214274714668913E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 3|1.6214274714668949E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 4|1.6214274714668982E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 5|1.6214274714711156E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 6|1.6214274714711192E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 7|1.6214274714711227E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 8|1.6214274714711251E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 9|1.6214274715168822E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53371.0| 66.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 10| 1.621427471516886E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53371.0| 66.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 11|1.6214274715168898E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53371.0| 66.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 12| 1.621427471516893E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53372.0| 66.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 13| 1.621427471516896E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53372.0| 66.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0|
 14|1.6214274715168989E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0|

In [0]:
print(dft.count())

#dft=dft.limit(20)

250407

In [0]:
print(dft.count())
dft.select(indexCol).show()
ta=covAnomaliasAgrupado(redecJerarquia,dft,dtCol,indexCol)
ta._aplica_modelos_niveles()
ta._dfNiveles.show()


250407
+---+
_c0|
+---+
 1|
 2|
 3|
 4|
 5|
 6|
 7|
 8|
 9|
 10|
 11|
 12|
 13|
 14|
 15|
 16|
 17|
 18|
 19|
 20|
+---+
only showing top 20 rows

NIVEL 0
VARIABLES ['_c0', 'eth_type', 'ip_src_host']
Vectorizar esto: ['_c0', 'frame_time_epoch', 'tcp_len', 'tcp_port', 'tcp_seq', 'frame_len', 'tcp_window_size_scalefactor', 'ip_len', 'tcp_window_size', 'tcp_seq_raw', 'vssmonitoring_srcport', 'frame_cap_len', 'eth_addr', 'eth_addr_resolved', 'eth_dst', 'eth_dst_resolved', 'eth_padding', 'eth_src', 'eth_src_resolved', 'eth_type', 'frame_interface_name', 'frame_protocols', 'ip_addr', 'ip_dsfield', 'ip_dst', 'ip_dst_host', 'ip_flags', 'ip_host', 'ip_src', 'ip_src_host', 'tcp_analysis', 'tcp_flags']
COLUMNAS VEC ['_c0', 'frame_time_epoch', 'tcp_len', 'tcp_port', 'tcp_seq', 'frame_len', 'tcp_window_size_scalefactor', 'ip_len', 'tcp_window_size', 'tcp_seq_raw', 'vssmonitoring_srcport', 'frame_cap_len', 'eth_addr', 'eth_addr_resolved', 'eth_dst', 'eth_dst_resolved', 'eth_padding', 'eth_src', 'eth_src_resolved', 'eth_type', 'frame_interface_name', 'frame_protocols', 'ip_addr', 'ip_dsfield', 'ip_dst', 'ip_dst_host', 'ip_flags', 'ip_host', 'ip_src', 'ip_src_host', 'tcp_analysis', 'tcp_flags', 'features']
+---+
_c0|
+---+
 1|
 2|
 3|
 4|
 5|
 6|
 7|
 8|
 9|
 10|
 11|
 12|
 13|
 14|
 15|
 16|
 17|
 18|
 19|
 20|
+---+
only showing top 20 rows

COLUMNAS SCAL ['_c0', 'frame_time_epoch', 'tcp_len', 'tcp_port', 'tcp_seq', 'frame_len', 'tcp_window_size_scalefactor', 'ip_len', 'tcp_window_size', 'tcp_seq_raw', 'vssmonitoring_srcport', 'frame_cap_len', 'eth_addr', 'eth_addr_resolved', 'eth_dst', 'eth_dst_resolved', 'eth_padding', 'eth_src', 'eth_src_resolved', 'eth_type', 'frame_interface_name', 'frame_protocols', 'ip_addr', 'ip_dsfield', 'ip_dst', 'ip_dst_host', 'ip_flags', 'ip_host', 'ip_src', 'ip_src_host', 'tcp_analysis', 'tcp_flags', 'features', 'scaledFeatures']
+---+
_c0|
+---+
 1|
 2|
 3|
 4|
 5|
 6|
 7|
 8|
 9|
 10|
+---+
only showing top 10 rows

Scaled
+----------+
prediction|
+----------+
 1|
 6|
 3|
 5|
 9|
 4|
 8|
 7|
 10|
 2|
 0|
+----------+

+---+
_c0|
+---+
 1|
 2|
 3|
 4|
 5|
 6|
 7|
 8|
 9|
 10|
 11|
 12|
 13|
 14|
 15|
 16|
 17|
 18|
 19|
 20|
+---+
only showing top 20 rows

LABELED ['_c0', 'frame_time_epoch', 'tcp_len', 'tcp_port', 'tcp_seq', 'frame_len', 'tcp_window_size_scalefactor', 'ip_len', 'tcp_window_size', 'tcp_seq_raw', 'vssmonitoring_srcport', 'frame_cap_len', 'eth_addr', 'eth_addr_resolved', 'eth_dst', 'eth_dst_resolved', 'eth_padding', 'eth_src', 'eth_src_resolved', 'eth_type', 'frame_interface_name', 'frame_protocols', 'ip_addr', 'ip_dsfield', 'ip_dst', 'ip_dst_host', 'ip_flags', 'ip_host', 'ip_src', 'ip_src_host', 'tcp_analysis', 'tcp_flags', 'vecFeatures', 'features', 'nivel_0']
NIVEL 1
VARIABLES ['_c0', 'eth_src_resolved', 'frame_cap_len', 'ip_len', 'tcp_len', 'tcp_seq_raw', 'tcp_window_size', 'tcp_window_size_scalefactor']
Vectorizar esto: ['_c0', 'frame_time_epoch', 'tcp_len', 'tcp_port', 'tcp_seq', 'frame_len', 'tcp_window_size_scalefactor', 'ip_len', 'tcp_window_size', 'tcp_seq_raw', 'vssmonitoring_srcport', 'frame_cap_len', 'eth_addr', 'eth_addr_resolved', 'eth_dst', 'eth_dst_resolved', 'eth_padding', 'eth_src', 'eth_src_resolved', 'eth_type', 'frame_interface_name', 'frame_protocols', 'ip_addr', 'ip_dsfield', 'ip_dst', 'ip_dst_host', 'ip_flags', 'ip_host', 'ip_src', 'ip_src_host', 'tcp_analysis', 'tcp_flags', 'vecFeatures', 'nivel_0']
COLUMNAS VEC ['_c0', 'frame_time_epoch', 'tcp_len', 'tcp_port', 'tcp_seq', 'frame_len', 'tcp_window_size_scalefactor', 'ip_len', 'tcp_window_size', 'tcp_seq_raw', 'vssmonitoring_srcport', 'frame_cap_len', 'eth_addr', 'eth_addr_resolved', 'eth_dst', 'eth_dst_resolved', 'eth_padding', 'eth_src', 'eth_src_resolved', 'eth_type', 'frame_interface_name', 'frame_protocols', 'ip_addr', 'ip_dsfield', 'ip_dst', 'ip_dst_host', 'ip_flags', 'ip_host', 'ip_src', 'ip_src_host', 'tcp_analysis', 'tcp_flags', 'vecFeatures', 'nivel_0', 'features']
+---+
_c0|
+---+
 1|
 2|
 3|
 4|
 5|
 6|
 7|
 8

In [0]:
ta._dfNiveles.show()

+---+--------------------+-------+--------+----------+---------+---------------------------+------+---------------+-------------+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+-------------------+-------+-------+-------+--------------------+-------+--------+
_c0| frame_time_epoch|tcp_len|tcp_port| tcp_seq|frame_len|tcp_window_size_scalefactor|ip_len|tcp_window_size| tcp_seq_raw|vssmonitoring_srcport|frame_cap_len|eth_addr|eth_addr_resolved|eth_dst|eth_dst_resolved|eth_padding|eth_src|eth_src_resolved|eth_type|frame_interface_name|frame_protocols|ip_addr|ip_dsfield|ip_dst|ip_dst_host|ip_flags|ip_host|ip_src|ip_src_host|tcp_analysis|tcp_flags| vecFeatures|nivel_0|nivel_1|nivel_2| features|nivel_3| group|
+---+--------------------+-------+--------+----------+---------+---------------------------+------+---------------+-------------+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+-------------------+-------+-------+-------+--------------------+-------+--------+
 1|1.6214274714668849E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 2|1.6214274714668913E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 3|1.6214274714668949E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 4|1.6214274714668982E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 5|1.6214274714711156E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 6|1.6214274714711192E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 7|1.6214274714711227E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 8|1.6214274714711251E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 9|1.6214274715168822E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53371.0| 66.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [3.0,2.0,53371.0]| 5| 0| 10|[0.01254252300004...| 0|5_0_10_0|
 10| 1.621427471516886E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53371.0| 66.0| 3.0| 3.0| 3.0| 3.0| 

In [0]:
ta._dfNiveles.toPandas().to_csv(os.path.join(modelsPath,"results",'dfNiveles{sufijo}.csv'))

/databricks/spark/python/pyspark/sql/pandas/conversion.py:93: UserWarning: toPandas attempted Arrow optimization because 'spark.sql.execution.arrow.pyspark.enabled' is set to true; however, failed by the reason below:
 Unable to convert the field vecFeatures. If this column is not necessary, you may consider dropping it or converting to primitive type before the conversion.
Context: Unsupported type in conversion to Arrow: VectorUDT
Attempting non-optimization as 'spark.sql.execution.arrow.pyspark.fallback.enabled' is set to true.
 warnings.warn(msg)

In [0]:
ta._modela_agrupado()
seq=ta._grouped


+--------+-----+
 group|count|
+--------+-----+
0_0_10_0| 7200|
 0_0_3_0|37506|
 0_0_7_0|28623|
 0_2_8_1|14368|
10_2_8_1| 844|
 1_0_0_0| 480|
 1_0_0_1| 4|
1_0_10_1| 20|
 1_1_1_0|29419|
 1_1_1_1| 3|
 2_1_5_0| 6414|
 2_1_5_1| 896|
 2_1_9_0| 716|
 2_1_9_1| 716|
 2_3_2_0| 2383|
 2_3_2_1| 2383|
 2_3_4_0| 2383|
 2_3_4_1| 2383|
3_0_10_0| 10|
3_0_10_1| 2|
+--------+-----+
only showing top 20 rows

AGRUPADO 
+--------------------+--------+-------+-------+-------+--------+-------+-------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+-------+--------+--------+-------+-------+-------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+
 frame_time_epoch|0_0_10_0|0_0_3_0|0_0_7_0|0_2_8_1|10_2_8_1|1_0_0_0|1_0_0_1|1_0_10_1|1_1_1_0|1_1_1_1|2_1_5_0|2_1_5_1|2_1_9_0|2_1_9_1|2_3_2_0|2_3_2_1|2_3_4_0|2_3_4_1|3_0_10_0|3_0_10_1|3_0_11_0|3_0_7_0|3_2_10_0|3_2_10_1|3_2_8_1|4_2_8_1|5_0_0_0|5_0_10_0|6_1_5_1|6_1_6_1|6_2_8_1|6_2_9_1|6_3_4_1|7_2_8_1|8_1_5_0|8_1_5_1|8_1_6_0|8_1_9_0|8_1_9_1|8_2_10_1|8_3_2_0|8_3_2_1|8_3_4_0|8_3_4_1|9_1_6_0|9_1_6_1|9_1_9_0|9_1_9_1|9_2_8_1|
+--------------------+--------+-------+-------+-------+--------+-------+-------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+-------+--------+--------+-------+-------+-------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+
1.6214274714668849E9| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274714668913E9| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274714668949E9| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274714668982E9| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274714711156E9| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274714711192E9| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274714711227E9| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274714711251E9| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274715168822E9| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
 1.621427471516886E9| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274715168898E9| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
 1.621427471516893E9| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
 1.621427471516896E9| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0|
1.6214274715168989E9| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 0| 1| 0| 0| 0| 0| 0| 0| 0| 0|

In [0]:
seq.show()

+--------------------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+--

In [0]:
seq.count()

Out[57]: 250407

In [0]:
ta._dfNiveles.show()

+---+--------------------+-------+--------+----------+---------+---------------------------+------+---------------+-------------+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+-------------------+-------+-------+-------+--------------------+-------+--------+
_c0| frame_time_epoch|tcp_len|tcp_port| tcp_seq|frame_len|tcp_window_size_scalefactor|ip_len|tcp_window_size| tcp_seq_raw|vssmonitoring_srcport|frame_cap_len|eth_addr|eth_addr_resolved|eth_dst|eth_dst_resolved|eth_padding|eth_src|eth_src_resolved|eth_type|frame_interface_name|frame_protocols|ip_addr|ip_dsfield|ip_dst|ip_dst_host|ip_flags|ip_host|ip_src|ip_src_host|tcp_analysis|tcp_flags| vecFeatures|nivel_0|nivel_1|nivel_2| features|nivel_3| group|
+---+--------------------+-------+--------+----------+---------+---------------------------+------+---------------+-------------+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+-------------------+-------+-------+-------+--------------------+-------+--------+
 1|1.6214274714668849E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 2|1.6214274714668913E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 3|1.6214274714668949E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 4|1.6214274714668982E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 5|1.6214274714711156E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 6|1.6214274714711192E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 7|1.6214274714711227E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 8|1.6214274714711251E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 9|1.6214274715168822E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53371.0| 66.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [3.0,2.0,53371.0]| 5| 0| 10|[0.01254252300004...| 0|5_0_10_0|
 10| 1.621427471516886E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53371.0| 66.0| 3.0| 3.0| 3.0| 3.0| 

In [0]:
anomalos=ta._anomalies(seq,ta._groupCenterList)
print(anomalos.columns)
anomalos.sort('outliers',ascending=False).show()

Busqueda de anomalias
['frame_time_epoch', '0_0_0_0', '0_0_0_1', '0_0_1_0', '0_0_1_1', '0_0_2_0', '0_0_2_1', '0_0_3_0', '0_0_3_1', '0_0_4_0', '0_0_4_1', '0_0_5_0', '0_0_5_1', '0_0_6_0', '0_0_6_1', '0_0_7_0', '0_0_7_1', '0_0_8_0', '0_0_8_1', '0_0_9_0', '0_0_9_1', '0_0_10_0', '0_0_10_1', '0_0_11_0', '0_0_11_1', '0_1_0_0', '0_1_0_1', '0_1_1_0', '0_1_1_1', '0_1_2_0', '0_1_2_1', '0_1_3_0', '0_1_3_1', '0_1_4_0', '0_1_4_1', '0_1_5_0', '0_1_5_1', '0_1_6_0', '0_1_6_1', '0_1_7_0', '0_1_7_1', '0_1_8_0', '0_1_8_1', '0_1_9_0', '0_1_9_1', '0_1_10_0', '0_1_10_1', '0_1_11_0', '0_1_11_1', '0_2_0_0', '0_2_0_1', '0_2_1_0', '0_2_1_1', '0_2_2_0', '0_2_2_1', '0_2_3_0', '0_2_3_1', '0_2_4_0', '0_2_4_1', '0_2_5_0', '0_2_5_1', '0_2_6_0', '0_2_6_1', '0_2_7_0', '0_2_7_1', '0_2_8_0', '0_2_8_1', '0_2_9_0', '0_2_9_1', '0_2_10_0', '0_2_10_1', '0_2_11_0', '0_2_11_1', '0_3_0_0', '0_3_0_1', '0_3_1_0', '0_3_1_1', '0_3_2_0', '0_3_2_1', '0_3_3_0', '0_3_3_1', '0_3_4_0', '0_3_4_1', '0_3_5_0', '0_3_5_1', '0_3_6_0', '0_3_6_1', '0_3_7_0', '0_3_7_1', '0_3_8_0', '0_3_8_1', '0_3_9_0', '0_3_9_1', '0_3_10_0', '0_3_10_1', '0_3_11_0', '0_3_11_1', '1_0_0_0', '1_0_0_1', '1_0_1_0', '1_0_1_1', '1_0_2_0', '1_0_2_1', '1_0_3_0', '1_0_3_1', '1_0_4_0', '1_0_4_1', '1_0_5_0', '1_0_5_1', '1_0_6_0', '1_0_6_1', '1_0_7_0', '1_0_7_1', '1_0_8_0', '1_0_8_1', '1_0_9_0', '1_0_9_1', '1_0_10_0', '1_0_10_1', '1_0_11_0', '1_0_11_1', '1_1_0_0', '1_1_0_1', '1_1_1_0', '1_1_1_1', '1_1_2_0', '1_1_2_1', '1_1_3_0', '1_1_3_1', '1_1_4_0', '1_1_4_1', '1_1_5_0', '1_1_5_1', '1_1_6_0', '1_1_6_1', '1_1_7_0', '1_1_7_1', '1_1_8_0', '1_1_8_1', '1_1_9_0', '1_1_9_1', '1_1_10_0', '1_1_10_1', '1_1_11_0', '1_1_11_1', '1_2_0_0', '1_2_0_1', '1_2_1_0', '1_2_1_1', '1_2_2_0', '1_2_2_1', '1_2_3_0', '1_2_3_1', '1_2_4_0', '1_2_4_1', '1_2_5_0', '1_2_5_1', '1_2_6_0', '1_2_6_1', '1_2_7_0', '1_2_7_1', '1_2_8_0', '1_2_8_1', '1_2_9_0', '1_2_9_1', '1_2_10_0', '1_2_10_1', '1_2_11_0', '1_2_11_1', '1_3_0_0', '1_3_0_1', '1_3_1_0', '1_3_1_1', '1_3_2_0', '1_3_2_1', '1_3_3_0', '1_3_3_1', '1_3_4_0', '1_3_4_1', '1_3_5_0', '1_3_5_1', '1_3_6_0', '1_3_6_1', '1_3_7_0', '1_3_7_1', '1_3_8_0', '1_3_8_1', '1_3_9_0', '1_3_9_1', '1_3_10_0', '1_3_10_1', '1_3_11_0', '1_3_11_1', '2_0_0_0', '2_0_0_1', '2_0_1_0', '2_0_1_1', '2_0_2_0', '2_0_2_1', '2_0_3_0', '2_0_3_1', '2_0_4_0', '2_0_4_1', '2_0_5_0', '2_0_5_1', '2_0_6_0', '2_0_6_1', '2_0_7_0', '2_0_7_1', '2_0_8_0', '2_0_8_1', '2_0_9_0', '2_0_9_1', '2_0_10_0', '2_0_10_1', '2_0_11_0', '2_0_11_1', '2_1_0_0', '2_1_0_1', '2_1_1_0', '2_1_1_1', '2_1_2_0', '2_1_2_1', '2_1_3_0', '2_1_3_1', '2_1_4_0', '2_1_4_1', '2_1_5_0', '2_1_5_1', '2_1_6_0', '2_1_6_1', '2_1_7_0', '2_1_7_1', '2_1_8_0', '2_1_8_1', '2_1_9_0', '2_1_9_1', '2_1_10_0', '2_1_10_1', '2_1_11_0', '2_1_11_1', '2_2_0_0', '2_2_0_1', '2_2_1_0', '2_2_1_1', '2_2_2_0', '2_2_2_1', '2_2_3_0', '2_2_3_1', '2_2_4_0', '2_2_4_1', '2_2_5_0', '2_2_5_1', '2_2_6_0', '2_2_6_1', '2_2_7_0', '2_2_7_1', '2_2_8_0', '2_2_8_1', '2_2_9_0', '2_2_9_1', '2_2_10_0', '2_2_10_1', '2_2_11_0', '2_2_11_1', '2_3_0_0', '2_3_0_1', '2_3_1_0', '2_3_1_1', '2_3_2_0', '2_3_2_1', '2_3_3_0', '2_3_3_1', '2_3_4_0', '2_3_4_1', '2_3_5_0', '2_3_5_1', '2_3_6_0', '2_3_6_1', '2_3_7_0', '2_3_7_1', '2_3_8_0', '2_3_8_1', '2_3_9_0', '2_3_9_1', '2_3_10_0', '2_3_10_1', '2_3_11_0', '2_3_11_1', '3_0_0_0', '3_0_0_1', '3_0_1_0', '3_0_1_1', '3_0_2_0', '3_0_2_1', '3_0_3_0', '3_0_3_1', '3_0_4_0', '3_0_4_1', '3_0_5_0', '3_0_5_1', '3_0_6_0', '3_0_6_1', '3_0_7_0', '3_0_7_1', '3_0_8_0', '3_0_8_1', '3_0_9_0', '3_0_9_1', '3_0_10_0', '3_0_10_1', '3_0_11_0', '3_0_11_1', '3_1_0_0', '3_1_0_1', '3_1_1_0', '3_1_1_1', '3_1_2_0', '3_1_2_1', '3_1_3_0', '3_1_3_1', '3_1_4_0', '3_1_4_1', '3_1_5_0', '3_1_5_1', '3_1_6_0', '3_1_6_1', '3_1_7_0', '3_1_7_1', '3_1_8_0', '3_1_8_1', '3_1_9_0', '3_1_9_1', '3_1_10_0', '3_1_10_1', '3_1_11_0', '3_1_11_1', '3_2_0_0', '3_2_0_1', '3_2_1_0', '3_2_1_1', '3_2_2_0', '3_2_2_1', '3_2_3_0', '3_2_3_1', '3_2_4_0', '3_2_4_1', '3_2_5_0', '3_2_5_1', '3_2_6_0', '3_2_6_1', '3_2_7_0', '3_2_7_1', '3_2_8_0', '3_2_8_1', '3_2_9_

In [0]:
seq

Out[60]: DataFrame[frame_time_epoch: double, 0_0_0_0: bigint, 0_0_0_1: bigint, 0_0_1_0: bigint, 0_0_1_1: bigint, 0_0_2_0: bigint, 0_0_2_1: bigint, 0_0_3_0: bigint, 0_0_3_1: bigint, 0_0_4_0: bigint, 0_0_4_1: bigint, 0_0_5_0: bigint, 0_0_5_1: bigint, 0_0_6_0: bigint, 0_0_6_1: bigint, 0_0_7_0: bigint, 0_0_7_1: bigint, 0_0_8_0: bigint, 0_0_8_1: bigint, 0_0_9_0: bigint, 0_0_9_1: bigint, 0_0_10_0: bigint, 0_0_10_1: bigint, 0_0_11_0: bigint, 0_0_11_1: bigint, 0_1_0_0: bigint, 0_1_0_1: bigint, 0_1_1_0: bigint, 0_1_1_1: bigint, 0_1_2_0: bigint, 0_1_2_1: bigint, 0_1_3_0: bigint, 0_1_3_1: bigint, 0_1_4_0: bigint, 0_1_4_1: bigint, 0_1_5_0: bigint, 0_1_5_1: bigint, 0_1_6_0: bigint, 0_1_6_1: bigint, 0_1_7_0: bigint, 0_1_7_1: bigint, 0_1_8_0: bigint, 0_1_8_1: bigint, 0_1_9_0: bigint, 0_1_9_1: bigint, 0_1_10_0: bigint, 0_1_10_1: bigint, 0_1_11_0: bigint, 0_1_11_1: bigint, 0_2_0_0: bigint, 0_2_0_1: bigint, 0_2_1_0: bigint, 0_2_1_1: bigint, 0_2_2_0: bigint, 0_2_2_1: bigint, 0_2_3_0: bigint, 0_2_3_1: bigint, 0_2_4_0: bigint, 0_2_4_1: bigint, 0_2_5_0: bigint, 0_2_5_1: bigint, 0_2_6_0: bigint, 0_2_6_1: bigint, 0_2_7_0: bigint, 0_2_7_1: bigint, 0_2_8_0: bigint, 0_2_8_1: bigint, 0_2_9_0: bigint, 0_2_9_1: bigint, 0_2_10_0: bigint, 0_2_10_1: bigint, 0_2_11_0: bigint, 0_2_11_1: bigint, 0_3_0_0: bigint, 0_3_0_1: bigint, 0_3_1_0: bigint, 0_3_1_1: bigint, 0_3_2_0: bigint, 0_3_2_1: bigint, 0_3_3_0: bigint, 0_3_3_1: bigint, 0_3_4_0: bigint, 0_3_4_1: bigint, 0_3_5_0: bigint, 0_3_5_1: bigint, 0_3_6_0: bigint, 0_3_6_1: bigint, 0_3_7_0: bigint, 0_3_7_1: bigint, 0_3_8_0: bigint, 0_3_8_1: bigint, 0_3_9_0: bigint, 0_3_9_1: bigint, 0_3_10_0: bigint, 0_3_10_1: bigint, 0_3_11_0: bigint, 0_3_11_1: bigint, 1_0_0_0: bigint, 1_0_0_1: bigint, 1_0_1_0: bigint, 1_0_1_1: bigint, 1_0_2_0: bigint, 1_0_2_1: bigint, 1_0_3_0: bigint, 1_0_3_1: bigint, 1_0_4_0: bigint, 1_0_4_1: bigint, 1_0_5_0: bigint, 1_0_5_1: bigint, 1_0_6_0: bigint, 1_0_6_1: bigint, 1_0_7_0: bigint, 1_0_7_1: bigint, 1_0_8_0: bigint, 1_0_8_1: bigint, 1_0_9_0: bigint, 1_0_9_1: bigint, 1_0_10_0: bigint, 1_0_10_1: bigint, 1_0_11_0: bigint, 1_0_11_1: bigint, 1_1_0_0: bigint, 1_1_0_1: bigint, 1_1_1_0: bigint, 1_1_1_1: bigint, 1_1_2_0: bigint, 1_1_2_1: bigint, 1_1_3_0: bigint, 1_1_3_1: bigint, 1_1_4_0: bigint, 1_1_4_1: bigint, 1_1_5_0: bigint, 1_1_5_1: bigint, 1_1_6_0: bigint, 1_1_6_1: bigint, 1_1_7_0: bigint, 1_1_7_1: bigint, 1_1_8_0: bigint, 1_1_8_1: bigint, 1_1_9_0: bigint, 1_1_9_1: bigint, 1_1_10_0: bigint, 1_1_10_1: bigint, 1_1_11_0: bigint, 1_1_11_1: bigint, 1_2_0_0: bigint, 1_2_0_1: bigint, 1_2_1_0: bigint, 1_2_1_1: bigint, 1_2_2_0: bigint, 1_2_2_1: bigint, 1_2_3_0: bigint, 1_2_3_1: bigint, 1_2_4_0: bigint, 1_2_4_1: bigint, 1_2_5_0: bigint, 1_2_5_1: bigint, 1_2_6_0: bigint, 1_2_6_1: bigint, 1_2_7_0: bigint, 1_2_7_1: bigint, 1_2_8_0: bigint, 1_2_8_1: bigint, 1_2_9_0: bigint, 1_2_9_1: bigint, 1_2_10_0: bigint, 1_2_10_1: bigint, 1_2_11_0: bigint, 1_2_11_1: bigint, 1_3_0_0: bigint, 1_3_0_1: bigint, 1_3_1_0: bigint, 1_3_1_1: bigint, 1_3_2_0: bigint, 1_3_2_1: bigint, 1_3_3_0: bigint, 1_3_3_1: bigint, 1_3_4_0: bigint, 1_3_4_1: bigint, 1_3_5_0: bigint, 1_3_5_1: bigint, 1_3_6_0: bigint, 1_3_6_1: bigint, 1_3_7_0: bigint, 1_3_7_1: bigint, 1_3_8_0: bigint, 1_3_8_1: bigint, 1_3_9_0: bigint, 1_3_9_1: bigint, 1_3_10_0: bigint, 1_3_10_1: bigint, 1_3_11_0: bigint, 1_3_11_1: bigint, 2_0_0_0: bigint, 2_0_0_1: bigint, 2_0_1_0: bigint, 2_0_1_1: bigint, 2_0_2_0: bigint, 2_0_2_1: bigint, 2_0_3_0: bigint, 2_0_3_1: bigint, 2_0_4_0: bigint, 2_0_4_1: bigint, 2_0_5_0: bigint, 2_0_5_1: bigint, 2_0_6_0: bigint, 2_0_6_1: bigint, 2_0_7_0: bigint, 2_0_7_1: bigint, 2_0_8_0: bigint, 2_0_8_1: bigint, 2_0_9_0: bigint, 2_0_9_1: bigint, 2_0_10_0: bigint, 2_0_10_1: bigint, 2_0_11_0: bigint, 2_0_11_1: bigint, 2_1_0_0: bigint, 2_1_0_1: bigint, 2_1_1_0: bigint, 2_1_1_1: bigint, 2_1_2_0: bigint, 2_1_2_1: bigint, 2_1_3_0: bigint, 2_1_3_1: bigint, 2_1_4_0: bigint, 2_1_4_1: bigint, 2_1_5_0: bigint, 2_1_5_1: bigint, 2_1_6_0: bigint, 2_1_6_1: bigint, 2_1_7_0: 

In [0]:
import gc
gc.collect()

Out[61]: 7553

In [0]:
seq2=seq.sample(withReplacement=False,fraction=0.75)

In [0]:
#ta=covAnomaliasAgrupado(redecJerarquia,dft,dtCol,indexCol)
#seq.show()
#anomalos.show()
dfAF=ta._anomaly_fields(seq2,anomalos)

['frame_time_epoch', '0_0_0_0', '0_0_0_1', '0_0_1_0', '0_0_1_1', '0_0_2_0', '0_0_2_1', '0_0_3_0', '0_0_3_1', '0_0_4_0', '0_0_4_1', '0_0_5_0', '0_0_5_1', '0_0_6_0', '0_0_6_1', '0_0_7_0', '0_0_7_1', '0_0_8_0', '0_0_8_1', '0_0_9_0', '0_0_9_1', '0_0_10_0', '0_0_10_1', '0_0_11_0', '0_0_11_1', '0_1_0_0', '0_1_0_1', '0_1_1_0', '0_1_1_1', '0_1_2_0', '0_1_2_1', '0_1_3_0', '0_1_3_1', '0_1_4_0', '0_1_4_1', '0_1_5_0', '0_1_5_1', '0_1_6_0', '0_1_6_1', '0_1_7_0', '0_1_7_1', '0_1_8_0', '0_1_8_1', '0_1_9_0', '0_1_9_1', '0_1_10_0', '0_1_10_1', '0_1_11_0', '0_1_11_1', '0_2_0_0', '0_2_0_1', '0_2_1_0', '0_2_1_1', '0_2_2_0', '0_2_2_1', '0_2_3_0', '0_2_3_1', '0_2_4_0', '0_2_4_1', '0_2_5_0', '0_2_5_1', '0_2_6_0', '0_2_6_1', '0_2_7_0', '0_2_7_1', '0_2_8_0', '0_2_8_1', '0_2_9_0', '0_2_9_1', '0_2_10_0', '0_2_10_1', '0_2_11_0', '0_2_11_1', '0_3_0_0', '0_3_0_1', '0_3_1_0', '0_3_1_1', '0_3_2_0', '0_3_2_1', '0_3_3_0', '0_3_3_1', '0_3_4_0', '0_3_4_1', '0_3_5_0', '0_3_5_1', '0_3_6_0', '0_3_6_1', '0_3_7_0', '0_3_7_1', '0_3_8_0', '0_3_8_1', '0_3_9_0', '0_3_9_1', '0_3_10_0', '0_3_10_1', '0_3_11_0', '0_3_11_1', '1_0_0_0', '1_0_0_1', '1_0_1_0', '1_0_1_1', '1_0_2_0', '1_0_2_1', '1_0_3_0', '1_0_3_1', '1_0_4_0', '1_0_4_1', '1_0_5_0', '1_0_5_1', '1_0_6_0', '1_0_6_1', '1_0_7_0', '1_0_7_1', '1_0_8_0', '1_0_8_1', '1_0_9_0', '1_0_9_1', '1_0_10_0', '1_0_10_1', '1_0_11_0', '1_0_11_1', '1_1_0_0', '1_1_0_1', '1_1_1_0', '1_1_1_1', '1_1_2_0', '1_1_2_1', '1_1_3_0', '1_1_3_1', '1_1_4_0', '1_1_4_1', '1_1_5_0', '1_1_5_1', '1_1_6_0', '1_1_6_1', '1_1_7_0', '1_1_7_1', '1_1_8_0', '1_1_8_1', '1_1_9_0', '1_1_9_1', '1_1_10_0', '1_1_10_1', '1_1_11_0', '1_1_11_1', '1_2_0_0', '1_2_0_1', '1_2_1_0', '1_2_1_1', '1_2_2_0', '1_2_2_1', '1_2_3_0', '1_2_3_1', '1_2_4_0', '1_2_4_1', '1_2_5_0', '1_2_5_1', '1_2_6_0', '1_2_6_1', '1_2_7_0', '1_2_7_1', '1_2_8_0', '1_2_8_1', '1_2_9_0', '1_2_9_1', '1_2_10_0', '1_2_10_1', '1_2_11_0', '1_2_11_1', '1_3_0_0', '1_3_0_1', '1_3_1_0', '1_3_1_1', '1_3_2_0', '1_3_2_1', '1_3_3_0', '1_3_3_1', '1_3_4_0', '1_3_4_1', '1_3_5_0', '1_3_5_1', '1_3_6_0', '1_3_6_1', '1_3_7_0', '1_3_7_1', '1_3_8_0', '1_3_8_1', '1_3_9_0', '1_3_9_1', '1_3_10_0', '1_3_10_1', '1_3_11_0', '1_3_11_1', '2_0_0_0', '2_0_0_1', '2_0_1_0', '2_0_1_1', '2_0_2_0', '2_0_2_1', '2_0_3_0', '2_0_3_1', '2_0_4_0', '2_0_4_1', '2_0_5_0', '2_0_5_1', '2_0_6_0', '2_0_6_1', '2_0_7_0', '2_0_7_1', '2_0_8_0', '2_0_8_1', '2_0_9_0', '2_0_9_1', '2_0_10_0', '2_0_10_1', '2_0_11_0', '2_0_11_1', '2_1_0_0', '2_1_0_1', '2_1_1_0', '2_1_1_1', '2_1_2_0', '2_1_2_1', '2_1_3_0', '2_1_3_1', '2_1_4_0', '2_1_4_1', '2_1_5_0', '2_1_5_1', '2_1_6_0', '2_1_6_1', '2_1_7_0', '2_1_7_1', '2_1_8_0', '2_1_8_1', '2_1_9_0', '2_1_9_1', '2_1_10_0', '2_1_10_1', '2_1_11_0', '2_1_11_1', '2_2_0_0', '2_2_0_1', '2_2_1_0', '2_2_1_1', '2_2_2_0', '2_2_2_1', '2_2_3_0', '2_2_3_1', '2_2_4_0', '2_2_4_1', '2_2_5_0', '2_2_5_1', '2_2_6_0', '2_2_6_1', '2_2_7_0', '2_2_7_1', '2_2_8_0', '2_2_8_1', '2_2_9_0', '2_2_9_1', '2_2_10_0', '2_2_10_1', '2_2_11_0', '2_2_11_1', '2_3_0_0', '2_3_0_1', '2_3_1_0', '2_3_1_1', '2_3_2_0', '2_3_2_1', '2_3_3_0', '2_3_3_1', '2_3_4_0', '2_3_4_1', '2_3_5_0', '2_3_5_1', '2_3_6_0', '2_3_6_1', '2_3_7_0', '2_3_7_1', '2_3_8_0', '2_3_8_1', '2_3_9_0', '2_3_9_1', '2_3_10_0', '2_3_10_1', '2_3_11_0', '2_3_11_1', '3_0_0_0', '3_0_0_1', '3_0_1_0', '3_0_1_1', '3_0_2_0', '3_0_2_1', '3_0_3_0', '3_0_3_1', '3_0_4_0', '3_0_4_1', '3_0_5_0', '3_0_5_1', '3_0_6_0', '3_0_6_1', '3_0_7_0', '3_0_7_1', '3_0_8_0', '3_0_8_1', '3_0_9_0', '3_0_9_1', '3_0_10_0', '3_0_10_1', '3_0_11_0', '3_0_11_1', '3_1_0_0', '3_1_0_1', '3_1_1_0', '3_1_1_1', '3_1_2_0', '3_1_2_1', '3_1_3_0', '3_1_3_1', '3_1_4_0', '3_1_4_1', '3_1_5_0', '3_1_5_1', '3_1_6_0', '3_1_6_1', '3_1_7_0', '3_1_7_1', '3_1_8_0', '3_1_8_1', '3_1_9_0', '3_1_9_1', '3_1_10_0', '3_1_10_1', '3_1_11_0', '3_1_11_1', '3_2_0_0', '3_2_0_1', '3_2_1_0', '3_2_1_1', '3_2_2_0', '3_2_2_1', '3_2_3_0', '3_2_3_1', '3_2_4_0', '3_2_4_1', '3_2_5_0', '3_2_5_1', '3_2_6_0', '3_2_6_1', '3_2_7_0', '3_2_7_1', '3_2_8_0', '3_2_8_1', '3_2_9_0', '3_2_9_1', '3_2_10

In [0]:
dfAF.show()

+--------------------+---------+-------+------------------+---------+-------+----------+---------+-------+----------+
 frame_time_epoch|Anomaly_0|Value_0| Distance_0|Anomaly_1|Value_1|Distance_1|Anomaly_2|Value_2|Distance_2|
+--------------------+---------+-------+------------------+---------+-------+----------+---------+-------+----------+
1.6214283923788047E9| 6_1_5_1| 1| 7.903049379689256| | | | | | |
 1.621428222408794E9| | | | | | | | | |
1.6214281320904183E9| | | | | | | | | |
1.6214282293625681E9| 0_2_8_1| 1| 4.05315167673956| | | | | | |
1.6214283857914028E9| | | | | | | | | |
1.6214280448322432E9| | | | | | | | | |
1.6214280938700676E9| 5_0_0_0| 1| 4.710174597001615| | | | | | |
1.6214281360893707E9| | | | | | | | | |
1.6214281120313385E9| 3_0_11_0| 1|3.2546696243810915| | | | | | |
 1.621428375702343E9| 3_2_8_1| 1| 4.294176790482101| | | | | | |
 1.62142818743263E9| 8_1_5_0| 1| 5.567833579289301| | | | | | |
1.6214279747228928E9| 0_2_8_1| 1| 4.05315167673956| | | | | | |
1.6214282666389463E9| | | | | | | | | |
 1.621428093425995E9| 9_1_6_0| 1| 4.763429377394285| | | | | | |
 1.621428119391821E9| | | | | | | | | |
1.6214279707012346E9| 3_2_8_1| 1| 4.294176790482101| | | | | | |
1.6214283449454863E9| 8_3_4_0| 1|11.899589563675354| | | | | | |
1.6214281007232552E9| 8_1_5_0| 1| 5.567833579289301| | | | | | |
1.6214282170321743E9| 3_0_11_0| 1|3.2546696243810915| | | | | | |
 1.621428328435164E9| 2_3_4_1| 1|10.201968195577672| | | | | | |
+--------------------+---------+-------+------------------+---------+-------+----------+---------+-------+----------+
only showing top 20 rows

In [0]:
dfAF.toPandas().to_csv(os.path.join(modelsPath,"results",f"Anomalias_grupo_{sufijo}.csv"))

In [0]:
ta._grouped.show()

+--------------------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+-------+--------+--------+--------+--------+-------+-------+-------+-------+-------+-------+-------+--

In [0]:
sufijo

Out[68]: '_2021'

In [0]:
GruposPorTiempo=anomalos.join(dfAF,[dtCol]).join(seq,[dtCol])

try:
    spark.sql(f"drop table GruposPorTiempo{sufijo}")
except:
    print(f"No existe la tabla GruposPorTiempo{sufijo}")

GruposPorTiempo.createOrReplaceTempView("mytempTable")
spark.sql(f"create table GruposPorTiempo{sufijo} as select * from mytempTable")
  

No existe la tabla GruposPorTiempo_2021
Out[69]: DataFrame[]

In [0]:
%sql

select * from GruposPorTiempo_26

timestamp distance outliers Anomaly_0 Value_0 Distance_0 Anomaly_1 Value_1 Distance_1 Anomaly_2 Value_2 Distance_2 0_0_0_0_0 0_0_0_0_1 0_0_0_0_2 0_0_0_1_0 0_0_0_1_1 0_0_0_1_2 0_0_0_2_0 0_0_0_2_1 0_0_0_2_2 0_0_0_3_0 0_0_0_3_1 0_0_0_3_2 0_0_0_4_0 0_0_0_4_1 0_0_0_4_2 0_0_0_5_0 0_0_0_5_1 0_0_0_5_2 0_0_0_6_0 0_0_0_6_1 0_0_0_6_2 0_0_1_0_0 0_0_1_0_1 0_0_1_0_2 0_0_1_1_0 0_0_1_1_1 0_0_1_1_2 0_0_1_2_0 0_0_1_2_1 0_0_1_2_2 0_0_1_3_0 0_0_1_3_1 0_0_1_3_2 0_0_1_4_0 0_0_1_4_1 0_0_1_4_2 0_0_1_5_0 0_0_1_5_1 0_0_1_5_2 0_0_1_6_0 0_0_1_6_1 0_0_1_6_2 0_1_0_0_0 0_1_0_0_1 0_1_0_0_2 0_1_0_1_0 0_1_0_1_1 0_1_0_1_2 0_1_0_2_0 0_1_0_2_1 0_1_0_2_2 0_1_0_3_0 0_1_0_3_1 0_1_0_3_2 0_1_0_4_0 0_1_0_4_1 0_1_0_4_2 0_1_0_5_0 0_1_0_5_1 0_1_0_5_2 0_1_0_6_0 0_1_0_6_1 0_1_0_6_2 0_1_1_0_0 0_1_1_0_1 0_1_1_0_2 0_1_1_1_0 0_1_1_1_1 0_1_1_1_2 0_1_1_2_0 0_1_1_2_1 0_1_1_2_2 0_1_1_3_0 0_1_1_3_1 0_1_1_3_2 0_1_1_4_0 0_1_1_4_1 0_1_1_4_2 0_1_1_5_0 0_1_1_5_1 0_1_1_5_2 0_1_1_6_0 0_1_1_6_1 0_1_1_6_2 0_2_0_0_0 0_2_0_0_1 0_2_0_0_2 0_2_0_1_0 0_2_0_1_1 0_2_0_1_2 0_2_0_2_0 0_2_0_2_1 0_2_0_2_2 0_2_0_3_0 0_2_0_3_1 0_2_0_3_2 0_2_0_4_0 0_2_0_4_1 0_2_0_4_2 0_2_0_5_0 0_2_0_5_1 0_2_0_5_2 0_2_0_6_0 0_2_0_6_1 0_2_0_6_2 0_2_1_0_0 0_2_1_0_1 0_2_1_0_2 0_2_1_1_0 0_2_1_1_1 0_2_1_1_2 0_2_1_2_0 0_2_1_2_1 0_2_1_2_2 0_2_1_3_0 0_2_1_3_1 0_2_1_3_2 0_2_1_4_0 0_2_1_4_1 0_2_1_4_2 0_2_1_5_0 0_2_1_5_1 0_2_1_5_2 0_2_1_6_0 0_2_1_6_1 0_2_1_6_2 0_3_0_0_0 0_3_0_0_1 0_3_0_0_2 0_3_0_1_0 0_3_0_1_1 0_3_0_1_2 0_3_0_2_0 0_3_0_2_1 0_3_0_2_2 0_3_0_3_0 0_3_0_3_1 0_3_0_3_2 0_3_0_4_0 0_3_0_4_1 0_3_0_4_2 0_3_0_5_0 0_3_0_5_1 0_3_0_5_2 0_3_0_6_0 0_3_0_6_1 0_3_0_6_2 0_3_1_0_0 0_3_1_0_1 0_3_1_0_2 0_3_1_1_0 0_3_1_1_1 0_3_1_1_2 0_3_1_2_0 0_3_1_2_1 0_3_1_2_2 0_3_1_3_0 0_3_1_3_1 0_3_1_3_2 0_3_1_4_0 0_3_1_4_1 0_3_1_4_2 0_3_1_5_0 0_3_1_5_1 0_3_1_5_2 0_3_1_6_0 0_3_1_6_1 0_3_1_6_2 0_4_0_0_0 0_4_0_0_1 0_4_0_0_2 0_4_0_1_0 0_4_0_1_1 0_4_0_1_2 0_4_0_2_0 0_4_0_2_1 0_4_0_2_2 0_4_0_3_0 0_4_0_3_1 0_4_0_3_2 0_4_0_4_0 0_4_0_4_1 0_4_0_4_2 0_4_0_5_0 0_4_0_5_1 0_4_0_5_2 0_4_0_6_0 0_4_0_6_1 0_4_0_6_2 0_4_1_0_0 0_4_1_0_1 0_4_1_0_2 0_4_1_1_0 0_4_1_1_1 0_4_1_1_2 0_4_1_2_0 0_4_1_2_1 0_4_1_2_2 0_4_1_3_0 0_4_1_3_1 0_4_1_3_2 0_4_1_4_0 0_4_1_4_1 0_4_1_4_2 0_4_1_5_0 0_4_1_5_1 0_4_1_5_2 0_4_1_6_0 0_4_1_6_1 0_4_1_6_2 1_0_0_0_0 1_0_0_0_1 1_0_0_0_2 1_0_0_1_0 1_0_0_1_1 1_0_0_1_2 1_0_0_2_0 1_0_0_2_1 1_0_0_2_2 1_0_0_3_0 1_0_0_3_1 1_0_0_3_2 1_0_0_4_0 1_0_0_4_1 1_0_0_4_2 1_0_0_5_0 1_0_0_5_1 1_0_0_5_2 1_0_0_6_0 1_0_0_6_1 1_0_0_6_2 1_0_1_0_0 1_0_1_0_1 1_0_1_0_2 1_0_1_1_0 1_0_1_1_1 1_0_1_1_2 1_0_1_2_0 1_0_1_2_1 1_0_1_2_2 1_0_1_3_0 1_0_1_3_1 1_0_1_3_2 1_0_1_4_0 1_0_1_4_1 1_0_1_4_2 1_0_1_5_0 1_0_1_5_1 1_0_1_5_2 1_0_1_6_0 1_0_1_6_1 1_0_1_6_2 1_1_0_0_0 1_1_0_0_1 1_1_0_0_2 1_1_0_1_0 1_1_0_1_1 1_1_0_1_2 1_1_0_2_0 1_1_0_2_1 1_1_0_2_2 1_1_0_3_0 1_1_0_3_1 1_1_0_3_2 1_1_0_4_0 1_1_0_4_1 1_1_0_4_2 1_1_0_5_0 1_1_0_5_1 1_1_0_5_2 1_1_0_6_0 1_1_0_6_1 1_1_0_6_2 1_1_1_0_0 1_1_1_0_1 1_1_1_0_2 1_1_1_1_0 1_1_1_1_1 1_1_1_1_2 1_1_1_2_0 1_1_1_2_1 1_1_1_2_2 1_1_1_3_0 1_1_1_3_1 1_1_1_3_2 1_1_1_4_0 1_1_1_4_1 1_1_1_4_2 1_1_1_5_0 1_1_1_5_1 1_1_1_5_2 1_1_1_6_0 1_1_1_6_1 1_1_1_6_2 1_2_0_0_0 1_2_0_0_1 1_2_0_0_2 1_2_0_1_0 1_2_0_1_1 1_2_0_1_2 1_2_0_2_0 1_2_0_2_1 1_2_0_2_2 1_2_0_3_0 1_2_0_3_1 1_2_0_3_2 1_2_0_4_0 1_2_0_4_1 1_2_0_4_2 1_2_0_5_0 1_2_0_5_1 1_2_0_5_2 1_2_0_6_0 1_2_0_6_1 1_2_0_6_2 1_2_1_0_0 1_2_1_0_1 1_2_1_0_2 1_2_1_1_0 1_2_1_1_1 1_2_1_1_2 1_2_1_2_0 1_2_1_2_1 1_2_1_2_2 1_2_1_3_0 1_2_1_3_1 1_2_1_3_2 1_2_1_4_0 1_2_1_4_1 1_2_1_4_2 1_2_1_5_0 1_2_1_5_1 1_2_1_5_2 1_2_1_6_0 1_2_1_6_1 1_2_1_6_2 1_3_0_0_0 1_3_0_0_1 1_3_0_0_2 1_3_0_1_0 1_3_0_1_1 1_3_0_1_2 1_3_0_2_0 1_3_0_2_1 1_3_0_2_2 1_3_0_3_0 1_3_0_3_1 1_3_0_3_2 1_3_0_4_0 1_3_0_4_1 1_3_0_4_2 1_3_0_5_0 1_3_0_5_1 1_3_0_5_2 1_3_0_6_0 1_3_0_6_1 1_3_0_6_2 1_3_1_0_0 1_3_1_0_1 1_3_1_0_2 1_3_1_1_0 1_3_1_1_1 1_3_1_1_2 1_3_1_2_0 1_3_1_2_1 1_3_1_2_2 1_3_1_3_0 1_3_1_3_1 1_3_1_3_2 1_3_1_4_0 1_3_1_4_1 1_3_1_4_2 1_3_1_5_0 1_3_1_5_1 1_3_1_5_2 1_3_1_6_0 1_3_1_6_1 1_3_1_6_2 1_4_0_0_0 1_4_0_0_1 1_4_0_0_2 1_4_0_1_0 1_4_0_1_1 1_4_0_1_2 1_4_0_2_0 1_4_0_2_1 1_4_0_2_2 1_4_0_3_0 1_4_0

In [0]:
ta._dfNiveles.show()
print(ta._dfNiveles.count())

+---+--------------------+-------+--------+----------+---------+---------------------------+------+---------------+-------------+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+-------------------+-------+-------+-------+--------------------+-------+--------+
_c0| frame_time_epoch|tcp_len|tcp_port| tcp_seq|frame_len|tcp_window_size_scalefactor|ip_len|tcp_window_size| tcp_seq_raw|vssmonitoring_srcport|frame_cap_len|eth_addr|eth_addr_resolved|eth_dst|eth_dst_resolved|eth_padding|eth_src|eth_src_resolved|eth_type|frame_interface_name|frame_protocols|ip_addr|ip_dsfield|ip_dst|ip_dst_host|ip_flags|ip_host|ip_src|ip_src_host|tcp_analysis|tcp_flags| vecFeatures|nivel_0|nivel_1|nivel_2| features|nivel_3| group|
+---+--------------------+-------+--------+----------+---------+---------------------------+------+---------------+-------------+---------------------+-------------+--------+-----------------+-------+----------------+-----------+-------+----------------+--------+--------------------+---------------+-------+----------+------+-----------+--------+-------+------+-----------+------------+---------+-------------------+-------+-------+-------+--------------------+-------+--------+
 1|1.6214274714668849E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 2|1.6214274714668913E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 3|1.6214274714668949E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 4|1.6214274714668982E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 5|1.6214274714711156E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 6|1.6214274714711192E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 7|1.6214274714711227E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 8|1.6214274714711251E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| -62370.0| 66.0| 7.0| 7.0| 0.0| 0.0| 7.0| 7.0| 7.0| 1.0| 0.0| 6.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [7.0,6.0,-62370.0]| 0| 2| 8|[1.53421672691047...| 1| 0_2_8_1|
 9|1.6214274715168822E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53371.0| 66.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 3.0| 2.0| 0.0| 2.0| 9.0| 1.0| 9.0| 9.0| 2.0| 9.0| 6.0| 6.0| 1.0| 2.0| [3.0,2.0,53371.0]| 5| 0| 10|[0.01254252300004...| 0|5_0_10_0|
 10| 1.621427471516886E9| -873.0|-49678.0|-1914902.0| 66.0| 1.0|-913.0| -65535.0|-3.63527823E9| 53371.0| 66.0| 3.0| 3.0| 3.0| 3.0| 

In [0]:
ta._dfNiveles.groupBy(dtCol,'group').show()

--------------------------------------------------------------------------- 
 AttributeError Traceback (most recent call last)
 <command-3196455714403697> in <module> 
 ----> 1 ta . _dfNiveles . groupBy ( dtCol , 'group' ) . show ( ) 

 AttributeError : 'GroupedData' object has no attribute 'show'